<a href="https://colab.research.google.com/github/mahekanna/Algo_setup/blob/main/Multi_verse_gann_s9_V1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.5 (Gann Logic Fixed) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'][i - 1]  # Use the previous day's closing price
        else:
            previous_price = price_data['close'][i - 1]  # Use the previous candle's closing price

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


#def resample_data(df, timeframe):
#    """
import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://5f55344bccd70d2f0a.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-8-906a750a7778>:348: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-8-906a750a7778>:348: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-8-906a750a7778>:99: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
<ipython-input-8-906a750a7778>:107: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://5f55344bccd70d2f0a.gradio.live


In [ ]:
pip install gradio

Above version is original. Below versions are mostly improvements

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.6 (NumPy Resampling) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'][i - 1]  # Use the previous day's closing price
        else:
            previous_price = price_data['close'][i - 1]  # Use the previous candle's closing price

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe using NumPy,
    aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Convert datetime index to NumPy datetime64 array
    dt_array = df.index.to_numpy(dtype='datetime64[ns]')

    # Calculate the resampling interval in nanoseconds
    interval_nanoseconds = pd.Timedelta(timeframe).value

    # Generate new timestamps for the resampled data
    start_time = dt_array[0].astype('datetime64[D]') + np.timedelta64(9, 'h') + np.timedelta64(15, 'm')  # 9:15 AM
    end_time = dt_array[-1]
    new_timestamps = np.arange(start_time, end_time, interval_nanoseconds, dtype='datetime64[ns]')

    # Create a new DataFrame with the resampled timestamps
    resampled_df = pd.DataFrame(index=new_timestamps)

    # Resample OHLCV data
    resampled_df['open'] = df['open'].resample(timeframe).first()
    resampled_df['high'] = df['high'].resample(timeframe).max()
    resampled_df['close'] = df['close'].resample(timeframe).last()
    resampled_df['volume'] = df['volume'].resample(timeframe).sum()

    # Drop any intervals that fall outside the market hours
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://11e23a2202724e9101.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-13-d8dfd163a9b2>:354: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  interval_nanoseconds = pd.Timedelta(timeframe).value
<ipython-input-13-d8dfd163a9b2>:365: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  resampled_df['open'] = df['open'].resample(timeframe).first()
<ipython-input-13-d8dfd163a9b2>:366: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  resampled_df['high'] = df['high'].resample(timeframe).max()
<ipython-input-13-d8dfd163a9b2>:367: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  resampled_df['close'] = df['close'].resample(timeframe).last()
<ipython-input-13-d8dfd163a9b2>:368: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  resampled_df['volume'] = df['volume'].resample(timeframe).sum()
<ipyth

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://11e23a2202724e9101.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.7 (Warnings Fixed)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc[]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")

    # Check if 'low' and 'open' columns exist in up DataFrame
    if 'low' in up.columns and 'open' in up.columns:
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    else:
        print("Error: 'low' or 'open' column not found in 'up' DataFrame.")

    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")

    # Check if 'low' and 'close' columns exist in down DataFrame
    if 'low' in down.columns and 'close' in down.columns:
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")
    else:
        print("Error: 'low' or 'close' column not found in 'down' DataFrame.")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe using NumPy,
    aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Convert datetime index to NumPy datetime64 array
    dt_array = df.index.to_numpy(dtype='datetime64[ns]')

    # Calculate the resampling interval in nanoseconds
    interval_nanoseconds = pd.Timedelta(timeframe.replace('H', 'h')).value  # Replace 'H' with 'h'

    # Generate new timestamps for the resampled data
    start_time = dt_array[0].astype('datetime64[D]') + np.timedelta64(9, 'h') + np.timedelta64(15, 'm')  # 9:15 AM
    end_time = dt_array[-1]
    new_timestamps = np.arange(start_time, end_time, interval_nanoseconds, dtype='datetime64[ns]')


    # Create a new DataFrame with the resampled timestamps
    resampled_df = pd.DataFrame(index=new_timestamps)

    # Resample OHLCV data (use lowercase 'h')
    resampled_df['open'] = df['open'].resample(timeframe.replace('H', 'h')).first()
    resampled_df['high'] = df['high'].resample(timeframe.replace('H', 'h')).max()
    resampled_df['close'] = df['close'].resample(timeframe.replace('H', 'h')).last()
    resampled_df['volume'] = df['volume'].resample(timeframe.replace('H', 'h')).sum()

    # Drop any intervals that fall outside the market hours
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://1a3d0375e1e910027a.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Error: 'low' or 'open' column not found in 'up' DataFrame.
Error: 'low' or 'close' column not found in 'down' DataFrame.
Chart saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h.png
PNL curve saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_pnl_curve.png
Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_trades.csv
Error: 'low' or 'open' column not found in 'up' DataFrame.
Error: 'low' or 'close' column not found in 'down' DataFrame.
Chart saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h.png
PNL curve saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_pnl_curve.png
Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_da

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.8 (Error Handling)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc[]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe using NumPy,
    aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Convert datetime index to NumPy datetime64 array
    dt_array = df.index.to_numpy(dtype='datetime64[ns]')

    # Calculate the resampling interval in nanoseconds
    interval_nanoseconds = pd.Timedelta(timeframe.replace('H', 'h')).value  # Replace 'H' with 'h'

    # Generate new timestamps for the resampled data
    start_time = dt_array[0].astype('datetime64[D]') + np.timedelta64(9, 'h') + np.timedelta64(15, 'm')  # 9:15 AM
    end_time = dt_array[-1]
    new_timestamps = np.arange(start_time, end_time, interval_nanoseconds, dtype='datetime64[ns]')

    # Create a new DataFrame with the resampled timestamps
    resampled_df = pd.DataFrame(index=new_timestamps)

    # Resample OHLCV data (use lowercase 'h')
    resampled_df['open'] = df['open'].resample(timeframe.replace('H', 'h')).first()
    resampled_df['high'] = df['high'].resample(timeframe.replace('H', 'h')).max()
    resampled_df['close'] = df['close'].resample(timeframe.replace('H', 'h')).last()
    resampled_df['volume'] = df['volume'].resample(timeframe.replace('H', 'h')).sum()

    # Drop any intervals that fall outside the market hours
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://668ef8f8cee3c2ed94.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-21 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 651.0, 'pnl': 2080.0}
{'entry_time': Timestamp('2023-11-23 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 656.64, 'targets': [663.06, 669.52, 676.0, 682.52], 'quantity': 76, 'exit_time': Timestamp('2023-11-24 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 679.0, 'pnl': 1699.360000000001}
{'entry_time': Timestamp('2023-11-24 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 682.52, 'targets': [689.06, 695.64, 702.25, 708.89], 'quantity': 73, 'exit_time': Timestamp('2023-12-01 09:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 730.7, 'pnl': 3517.140000000005}
{'entry_time': Timestamp('2023-12-01 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 735.77, 'targets': [742.56, 749.39, 756.25, 763.14], 'quantity': 67, 'exit_time': Times

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://668ef8f8cee3c2ed94.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.9 (Simplified)      ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc[]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe,
    aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample OHLCV data directly using the datetime index
    resampled_df = df.resample(timeframe.replace('H', 'h')).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    })

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
   """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f338c48689ccad36df.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-21 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 651.0, 'pnl': 2080.0}
{'entry_time': Timestamp('2023-11-23 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 656.64, 'targets': [663.06, 669.52, 676.0, 682.52], 'quantity': 76, 'exit_time': Timestamp('2023-11-24 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 679.0, 'pnl': 1699.360000000001}
{'entry_time': Timestamp('2023-11-24 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 682.52, 'targets': [689.06, 695.64, 702.25, 708.89], 'quantity': 73, 'exit_time': Timestamp('2023-12-01 09:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 730.7, 'pnl': 3517.140000000005}
{'entry_time': Timestamp('2023-12-01 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 735.77, 'targets': [742.56, 749.39, 756.25, 763.14], 'quantity': 67, 'exit_time': Times

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.0 (Final)           ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc[]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample OHLCV data directly using the datetime index
    resampled_df = df.resample(timeframe.replace('H', 'h')).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    })

    # Ensure a candle starts at 9:15 AM:
    for day in resampled_df.index.date:
        timestamp = pd.Timestamp(day.year, day.month, day.day, 9, 15, tz='Asia/Kolkata')
        if timestamp not in resampled_df.index:
            # If no data at 9:15, create a new row with previous day's close
            prev_day_close = df['close'].loc[df.index < timestamp].iloc[-1]
            new_row = pd.DataFrame({'open': prev_day_close, 'high': prev_day_close,
                                     'low': prev_day_close, 'close': prev_day_close,
                                     'volume': 0}, index=[timestamp])
            resampled_df = pd.concat([resampled_df, new_row]).sort_index()

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://72255e20cfb2018d35.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://72255e20cfb2018d35.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.1 (IndexError Fix)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc[]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc[]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample OHLCV data directly using the datetime index
    resampled_df = df.resample(timeframe.replace('H', 'h')).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    })

    # Ensure a candle starts at 9:15 AM:
    for day in resampled_df.index.date:
        timestamp = pd.Timestamp(day.year, day.month, day.day, 9, 15, tz='Asia/Kolkata')
        if timestamp not in resampled_df.index:
            # If no data at 9:15:
            prev_day_data = df['close'].loc[df.index < timestamp]
            if not prev_day_data.empty:
               prev_day_close = prev_day_data.iloc[-1]
            else:
                prev_day_close = df['close'].iloc[0]  # Use the first close of the day

                new_row = pd.DataFrame({'open': prev_day_close, 'high': prev_day_close,
                                     'low': prev_day_close, 'close': prev_day_close,
                                     'volume': 0}, index=[timestamp])
            resampled_df = pd.concat([resampled_df, new_row]).sort_index()

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f8652ca82ba14a1127.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://f8652ca82ba14a1127.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.2 (ValueError Fix)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    handling missing previous day's close.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Handle missing previous day's close:
        try:
            if current_date != previous_date:
                previous_price = price_data['close'].loc[previous_date]
            else:
                previous_price = price_data['close'].iloc[i - 1]
        except KeyError:
            continue  # Skip to the next iteration if previous price is not available

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []  # Initialize as a list
    short_pnl = []  # Initialize as a list
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)  # Append to the list
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)  # Append to the list

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Now works correctly with a list
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample OHLCV data directly using the datetime index
    resampled_df = df.resample(timeframe.replace('H', 'h')).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    })

    # Ensure a candle starts at 9:15 AM:
    for day in resampled_df.index.date:
        timestamp = pd.Timestamp(day.year, day.month, day.day, 9, 15, tz='Asia/Kolkata')
        if timestamp not in resampled_df.index:
            # If no data at 9:15:
            prev_day_data = df['close'].loc[df.index < timestamp]
            if not prev_day_data.empty:
                prev_day_close = prev_day_data.iloc[-1]
            else:
                prev_day_close = df['close'].iloc[0]  # Use the first close of the day

            new_row = pd.DataFrame({'open': prev_day_close, 'high': prev_day_close,
                                     'low': prev_day_close, 'close': prev_day_close,
                                     'volume': 0}, index=[timestamp])
            resampled_df = pd.concat([resampled_df, new_row]).sort_index()

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://914bc191708e97ec23.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-03 09:15:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-03 09:15:00+0530', tz='Asia/Kolkata'), 'exit_price': 1325.95, 'pnl': 56076.0}
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-08 09:15:00+0530', tz='Asia/Kolkata'), 'exit_price': 629.0, 'pnl': 320.0}
{'entry_time': Timestamp('2023-11-08 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 631.27, 'targets': [637.56, 643.89, 650.25, 656.64], 'quantity': 79, 'exit_time': Timestamp('2023-11-08 10:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 639.45, 'pnl': 646.220000000005}
{'entry_time': Timestamp('2023-11-15 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 631.27, 'targets': [637.56, 643.89, 650.25, 656.64], 'quantity': 79, 'exit_time': Timestamp('202

<ipython-input-21-1c409914ac74>:299: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))


Chart saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h.png
PNL curve saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_pnl_curve.png
Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_trades.csv
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://914bc191708e97ec23.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.3 (9:15 AM Fix)      ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    explicitly handling the 9:15 AM candle.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        previous_date = price_data.index[i - 1].date()

        # Explicitly check for the 9:15 AM candle:
        if current_time == datetime.time(9, 15):
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue  # Skip if previous day's close is not available
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []  # Initialize as a list
    short_pnl = []  # Initialize as a list
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)  # Append to the list
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)  # Append to the list

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Now works correctly with a list
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample OHLCV data directly using the datetime index
    resampled_df = df.resample(timeframe.replace('H', 'h')).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    })

    # Ensure a candle starts at 9:15 AM:
    for day in resampled_df.index.date:
        timestamp = pd.Timestamp(day.year, day.month, day.day, 9, 15, tz='Asia/Kolkata')
        if timestamp not in resampled_df.index:
           # If no data at 9:15:
            prev_day_data = df['close'].loc[df.index < timestamp]
            if not prev_day_data.empty:
                prev_day_close = prev_day_data.iloc[-1]
            else:
                prev_day_close = df['close'].iloc[0]  # Use the first close of the day

            new_row = pd.DataFrame({'open': prev_day_close, 'high': prev_day_close,
                                     'low': prev_day_close, 'close': prev_day_close,
                                     'volume': 0}, index=[timestamp])
            resampled_df = pd.concat([resampled_df, new_row]).sort_index()

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f430ab837d7f6421d0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-08 10:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 639.45, 'pnl': 1156.0000000000036}
{'entry_time': Timestamp('2023-11-09 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 631.27, 'targets': [637.56, 643.89, 650.25, 656.64], 'quantity': 79, 'exit_time': Timestamp('2023-11-13 10:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 638.6, 'pnl': 579.0700000000032}
{'entry_time': Timestamp('2023-11-15 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 631.27, 'targets': [637.56, 643.89, 650.25, 656.64], 'quantity': 79, 'exit_time': Timestamp('2023-11-15 10:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 639.95, 'pnl': 685.720000000005}
{'entry_time': Timestamp('2023-11-15 13:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 643.89, 'targets': [650.25, 656.64, 663.06, 669.52], 'quantity': 77, 'exi

<ipython-input-22-870e403f6a62>:299: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))


Chart saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h.png
PNL curve saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_pnl_curve.png
Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/AMARAJ/AMARAJ_1h_trades.csv
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://f430ab837d7f6421d0.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (dateutil)        ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule as rrule  # Import rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    explicitly handling the 9:15 AM candle.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        previous_date = price_data.index[i - 1].date()

        # Explicitly check for the 9:15 AM candle:
        if current_time == datetime.time(9, 15):
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue  # Skip if previous day's close is not available
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []  # Initialize as a list
    short_pnl = []  # Initialize as a list
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)  # Append to the list
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)  # Append to the list

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Now works correctly with a list
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    # Check if 'up' DataFrame is not empty
    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    # Check if 'down' DataFrame is not empty
    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the chart
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)  # Close the figure to free up memory

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save the PnL curve
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe using dateutil,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Calculate the resampling frequency
    freq = {'5min': rrule.MINUTELY, '15min': rrule.MINUTELY,
            '30min': rrule.MINUTELY, '1h': rrule.HOURLY}[timeframe]
    interval = {'5min': 5, '15min': 15, '30min': 30, '1h': 1}[timeframe]

    # Generate resampling timestamps using rrule
    start_date = df.index[0].date()
    end_date = df.index[-1].date()
    resampled_timestamps = list(rrule.rrule(
       freq=freq,
        interval=interval,
        dtstart=datetime.datetime(start_date.year, start_date.month, start_date.day, 9, 15, tzinfo=df.index.tz),
        until=datetime.datetime(end_date.year, end_date.month, end_date.day, 15, 30, tzinfo=df.index.tz)
    ))

    # Create a new DataFrame with the resampled timestamps
    resampled_df = pd.DataFrame(index=resampled_timestamps)

    # Resample OHLCV data
    resampled_df['open'] = df['open'].resample(timeframe.replace('H', 'h')).first()
    resampled_df['high'] = df['high'].resample(timeframe.replace('H', 'h')).max()
    resampled_df['low'] = df['low'].resample(timeframe.replace('H', 'h')).min()
    resampled_df['close'] = df['close'].resample(timeframe.replace('H', 'h')).last()
    resampled_df['volume'] = df['volume'].resample(timeframe.replace('H', 'h')).sum()

    # Drop any intervals that fall outside the market hours (if necessary)
    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Print some trade details
    print("Long Trades:")
    for trade in long_trades[:5]:  # Print the first 5 long trades
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:  # Print the first 5 short trades
        print(trade)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://4c5ce275927a88b22a.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-21 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 651.0, 'pnl': 2080.0}
{'entry_time': Timestamp('2023-11-23 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 656.64, 'targets': [663.06, 669.52, 676.0, 682.52], 'quantity': 76, 'exit_time': Timestamp('2023-11-24 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 679.0, 'pnl': 1699.360000000001}
{'entry_time': Timestamp('2023-11-24 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 682.52, 'targets': [689.06, 695.64, 702.25, 708.89], 'quantity': 73, 'exit_time': Timestamp('2023-12-01 09:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 730.7, 'pnl': 3517.140000000005}
{'entry_time': Timestamp('2023-12-01 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 735.77, 'targets': [742.56, 749.39, 756.25, 763.14], 'quantity': 67, 'exit_time': Times

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.2 (Logic Corrected) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule as rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    correctly using previous day's close for the first candle and
    previous candle's close for subsequent candles.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        if current_date != previous_date:  # First candle of the day
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue  # Skip if previous day's close is not available
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []  # Initialize as a list
    short_pnl = []  # Initialize as a list
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp in signals:
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                # Assuming you have a function to calculate quantity
                entry_quantity = calculate_quantity(capital=10000, entry_price=entry_price,
                                                    risk_percentage=1, stop_loss_price=entry_level * 0.99)
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': entry_quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                # Assuming you have a function to calculate quantity
                entry_quantity = calculate_quantity(capital=10000, entry_price=entry_price,
                                                    risk_percentage=1, stop_loss_price=entry_level * 1.01)
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': entry_quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate
                all_pnls.append(pnl)
                if position == 1:
                    long_pnl.append(pnl)  # Append to the long_pnl list
                    metrics['long_trades'] += 1
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                else:
                    short_pnl.append(pnl)  # Append to the short_pnl list
                    metrics['short_trades'] += 1
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['winning_long_trades'] = sum(1 for pnl in long_pnl if pnl > 0)
    metrics['winning_short_trades'] = sum(1 for pnl in short_pnl if pnl > 0)
    metrics['losing_long_trades'] = sum(1 for pnl in long_pnl if pnl < 0)
    metrics['losing_short_trades'] = sum(1 for pnl in short_pnl if pnl < 0)
    metrics['long_win_rate'] = metrics['winning_long_trades'] / metrics['long_trades'] if metrics['long_trades'] else 0
    metrics['short_win_rate'] = metrics['winning_short_trades'] / metrics['short_trades'] if metrics['short_trades'] else 0
    metrics['total_pnl'] = sum(all_pnls)
    metrics['long_pnl'] = sum(long_pnl)  # Calculate total long PnL
    metrics['short_pnl'] = sum(short_pnl)  # Calculate total short PnL
    metrics['avg_long_pnl'] = np.mean(long_pnl) if long_pnl else 0
    metrics['avg_short_pnl'] = np.mean(short_pnl) if short_pnl else 0
    metrics['max_long_pnl'] = np.max(long_pnl) if long_pnl else 0
    metrics['max_short_pnl'] = np.max(short_pnl) if short_pnl else 0
    metrics['min_long_pnl'] = np.min(long_pnl) if long_pnl else 0
    metrics['min_short_pnl'] = np.min(short_pnl) if short_pnl else 0
    metrics['sharpe_ratio'] = np.mean(all_pnls) / np.std(all_pnls) if all_pnls else 0
    metrics['sortino_ratio'] = np.mean(all_pnls) / np.std([pnl for pnl in all_pnls if pnl < 0]) if all_pnls and any(pnl < 0 for pnl in all_pnls) else 0
    metrics['max_drawdown'] = max(0, max(all_pnls) - min(all_pnls)) if all_pnls else 0

    # Add more metrics as needed

    return metrics, long_trades, short_trades

# ... (rest of your code)
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')  # Use '1h'
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.3 (Gradio Added)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import numpy as np
from scipy.stats import skew, kurtosis
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    correctly using previous day's close for the first candle and
    previous candle's close for subsequent candles.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        if current_date != previous_date:  # First candle of the day
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue  # Skip if previous day's close is not available
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []  # Initialize as a list
    short_pnl = []  # Initialize as a list
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp in signals:
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                # Assuming you have a function to calculate quantity
                entry_quantity = calculate_quantity(capital=10000, entry_price=entry_price,
                                                    risk_percentage=1, stop_loss_price=entry_level * 0.99)
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': entry_quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                # Assuming you have a function to calculate quantity
                entry_quantity = calculate_quantity(capital=10000, entry_price=entry_price,
                                                    risk_percentage=1, stop_loss_price=entry_level * 1.01)
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': entry_quantity})
            elif signal == 'exit_buy' and position == 1:
                exit_price = entry_level
                exit_time = timestamp
                pnl = (exit_price - entry_price) * long_trades[-1]['quantity']
                long_pnl.append(pnl)  # Append to the long_pnl list
                all_pnls.append(pnl)  # Append to the all_pnls list
                metrics['long_trades'] += 1
                metrics['long_wins'] += 1 if pnl > 0 else 0
                metrics['long_losses'] += 1 if pnl < 0 else 0
                position = 0
            elif signal == 'exit_sell' and position == -1:
                exit_price = entry_level
                exit_time = timestamp
                pnl = (entry_price - exit_price) * short_trades[-1]['quantity']
                short_pnl.append(pnl)  # Append to the short_pnl list
                all_pnls.append(pnl)  # Append to the all_pnls list
                metrics['short_trades'] += 1
                metrics['short_wins'] += 1 if pnl > 0 else 0
                metrics['short_losses'] += 1 if pnl < 0 else 0
                position = 0
        except IndexError:
            print(f"IndexError encountered at signal: {signal}, timestamp: {timestamp}")
            continue  # Continue to the next iteration

    # Calculate metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_wins'] = metrics['long_wins'] + metrics['short_wins']
    metrics['total_losses'] = metrics['long_losses'] + metrics['short_losses']
    if metrics['total_trades'] > 0:
        metrics['win_rate'] = metrics['total_wins'] / metrics['total_trades'] * 100
    if len(all_pnls) > 0:
        metrics['average_pnl'] = np.mean(all_pnls)
        metrics['max_pnl'] = np.max(all_pnls)
        metrics['min_pnl'] = np.min(all_pnls)
        metrics['sharpe_ratio'] = np.mean(all_pnls) / np.std(all_pnls) if np.std(all_pnls) != 0 else 0
        metrics['sortino_ratio'] = np.mean(all_pnls) / np.std([pnl for pnl in all_pnls if pnl < 0]) if any(pnl < 0 for pnl in all_pnls) else 0
        metrics['skew'] = skew(all_pnls)
        metrics['kurtosis'] = kurtosis(all_pnls)

    return metrics, long_pnl, short_pnl  # Return PnL lists as well


def backtest_gann(data, timeframe='5min'):
    """
    Backtests the Gann strategy on the provided data.

    Args:
        data: A pandas DataFrame with 'close' price data and a datetime index.
        timeframe: The timeframe of the data ('5min', '15min', etc.).

    Returns:
        A dictionary of trading metrics.
    """
    price_data = data.copy()
    signals = gann_strategy(price_data, timeframe)
    metrics, long_pnl, short_pnl = calculate_metrics(signals, price_data)  # Get PnL lists
    return metrics, signals, long_pnl, short_pnl

def plot_gann_signals(data, signals, timeframe='5min'):
    """
    Plots the Gann signals on the price chart.

    Args:
        data: A pandas DataFrame with 'close' price data and a datetime index.
        signals: A list of signals generated by the gann_strategy function.
        timeframe: The timeframe of the data ('5min', '15min', etc.).
    """
    plt.figure(figsize=(12, 6))
    plt.plot(data['close'], label='Close Price')

    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            plt.scatter(timestamp, entry_level, marker='^', color='green', label='Buy')
            for target in targets:
                plt.hlines(target, xmin=timestamp, xmax=data.index[-1], colors='green', linestyles='dashed', alpha=0.5)
        elif signal == 'sell':
            plt.scatter(timestamp, entry_level, marker='v', color='red', label='Sell')
            for target in targets:
                plt.hlines(target, xmin=timestamp, xmax=data.index[-1], colors='red', linestyles='dashed', alpha=0.5)

    plt.title(f'Gann Square of 9 Signals ({timeframe})')
    plt.xlabel('Date')
    plt.ylabel('Price')
    plt.legend()
    plt.tight_layout()
    # plt.show()  # Remove plt.show() here

def plot_equity_curve(long_pnl, short_pnl):
    """
    Plots the equity curve for long and short trades separately.

    Args:
        long_pnl: A list of PnLs for long trades.
        short_pnl: A list of PnLs for short trades.
    """
    plt.figure(figsize=(12, 6))

    # Calculate cumulative PnL for long and short trades
    cumulative_long_pnl = np.cumsum(long_pnl)
    cumulative_short_pnl = np.cumsum(short_pnl)

    plt.plot(cumulative_long_pnl, label='Long Equity Curve', color='green')
    plt.plot(cumulative_short_pnl, label='Short Equity Curve', color='red')

    plt.title('Equity Curves for Long and Short Trades')
    plt.xlabel('Trade Number')
    plt.ylabel('Cumulative PnL')
    plt.legend()
    plt.tight_layout()
    # plt.show()  # Remove plt.show() here

def optimize_gann(data, timeframes):
    """
    Optimizes the Gann strategy for different timeframes.

    Args:
        data: A pandas DataFrame with 'close' price data and a datetime index.
        timeframes: A list of timeframes to optimize for ('5min', '15min', etc.).

    Returns:
        A dictionary of optimal metrics for each timeframe.
    """
    optimal_metrics = {}
    for timeframe in timeframes:
        resampled_data = data['close'].resample(timeframe).last().dropna()
        metrics, signals, _, _ = backtest_gann(resampled_data, timeframe)
        optimal_metrics[timeframe] = metrics
    return optimal_metrics


def run_gann_analysis(data_path, timeframe='5min'):
    """
    Loads data, runs the Gann strategy, and returns metrics and plots.
    """
    try:
        data = pd.read_csv(data_path, index_col='datetime', parse_dates=True)
        resampled_data = data['close'].resample(timeframe).last().dropna()
        metrics, signals, long_pnl, short_pnl = backtest_gann(resampled_data, timeframe)

        # Generate plots
        plot_gann_signals(resampled_data, signals, timeframe)
        plt.savefig("gann_signals_plot.png")  # Save the signals plot
        plot_equity_curve(long_pnl, short_pnl)
        plt.savefig("equity_curve_plot.png")  # Save the equity curve plot

        return metrics, "gann_signals_plot.png", "equity_curve_plot.png"
    except Exception as e:
        return str(e), None, None

iface = gr.Interface(
    fn=run_gann_analysis,
    inputs=[
        gr.File(label="Upload CSV data file"),
        gr.Dropdown(['5min', '15min', '30min', '1H'], label="Timeframe", value='5min')
    ],
    outputs=[
        gr.Textbox(label="Metrics"),
        gr.Image(label="Gann Signals Plot", type="filepath"),
        gr.Image(label="Equity Curve Plot", type="filepath")
    ],
    title="Gann Square of 9 Strategy Backtesting",
    description="Upload your CSV data with 'datetime' and 'close' columns to backtest the strategy."
)

if __name__ == "__main__":
    iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://92133b01e1805e02b1.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://92133b01e1805e02b1.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.1 (Resampling Fix)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule as rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    explicitly handling the 9:15 AM candle.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        previous_date = price_data.index[i - 1].date()

        if current_time == datetime.time(9, 15):
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        try:
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
                all_pnls.append(pnl)

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        os.makedirs(save_path, exist_ok=True)
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        os.makedirs(save_path, exist_ok=True)
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe using dateutil,
    aligned with Indian market hours (9:15 - 15:30),
    and ensures a candle starts at 9:15 AM.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    freq = {'5min': rrule.MINUTELY, '15min': rrule.MINUTELY,
            '30min': rrule.MINUTELY, '1h': rrule.HOURLY}[timeframe]
    interval = {'5min': 5, '15min': 15, '30min': 30, '1h': 1}[timeframe]

    start_date = df.index[0].date()
    end_date = df.index[-1].date()
    resampled_timestamps = list(rrule.rrule(
        freq=freq,
        interval=interval,
        dtstart=datetime.datetime(start_date.year, start_date.month, start_date.day, 9, 15, tzinfo=df.index.tz),
        until=datetime.datetime(end_date.year, end_date.month, end_date.day, 15, 30, tzinfo=df.index.tz)
    ))

    resampled_df = pd.DataFrame(index=resampled_timestamps)

    resampled_df['open'] = df['open'].resample(timeframe.replace('H', 'h')).first()
    resampled_df['high'] = df['high'].resample(timeframe.replace('H', 'h')).max()
    resampled_df['low'] = df['low'].resample(timeframe.replace('H', 'h')).min()
    resampled_df['close'] = df['close'].resample(timeframe.replace('H', 'h')).last()
    resampled_df['volume'] = df['volume'].resample(timeframe.replace('H', 'h')).sum()

    resampled_df = resampled_df.dropna(subset=['open', 'close'])

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df, timeframe)

    signals = gann_strategy(resampled_df, timeframe)

    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    print("Long Trades:")
    for trade in long_trades[:5]:
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:
        print(trade)

    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)
        trade['cumulative_profit'] = cumulative_profit

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        os.makedirs(save_path, exist_ok=True)

        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---

stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000
risk_percentage = 1

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://77566a29f0180def80.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Long Trades:
{'entry_time': Timestamp('2023-11-06 14:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 625.0, 'targets': [631.27, 637.56, 643.89, 650.25], 'quantity': 80, 'exit_time': Timestamp('2023-11-21 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 651.0, 'pnl': 2080.0}
{'entry_time': Timestamp('2023-11-23 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 656.64, 'targets': [663.06, 669.52, 676.0, 682.52], 'quantity': 76, 'exit_time': Timestamp('2023-11-24 11:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 679.0, 'pnl': 1699.360000000001}
{'entry_time': Timestamp('2023-11-24 12:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 682.52, 'targets': [689.06, 695.64, 702.25, 708.89], 'quantity': 73, 'exit_time': Timestamp('2023-12-01 09:00:00+0530', tz='Asia/Kolkata'), 'exit_price': 730.7, 'pnl': 3517.140000000005}
{'entry_time': Timestamp('2023-12-01 10:00:00+0530', tz='Asia/Kolkata'), 'entry_price': 735.77, 'targets': [742.56, 749.39, 756.25, 763.14], 'quantity': 67, 'exit_time': Times

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.2 (Candle Fix)      ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule as rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    explicitly handling the 9:15 AM candle.
    """
    signals = []
    price_tolerance = 0.01  # Introduce a price tolerance

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        previous_date = price_data.index[i - 1].date()

        if current_time == datetime.time(9, 15):
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above - price_tolerance:  # Apply tolerance
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below + price_tolerance:  # Apply tolerance
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target - price_tolerance:  # Apply tolerance
                    # Find closest timestamp
                    closest_timestamp = price_data.index[price_data.index.get_loc(timestamp, method='nearest')]
                    signals.append(('exit_buy', target, j+1, closest_timestamp))

        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target + price_tolerance:  # Apply tolerance
                    # Find closest timestamp
                    closest_timestamp = price_data.index[price_data.index.get_loc(timestamp, method='nearest')]
                    signals.append(('exit_sell', target, j+1, closest_timestamp))

    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        try:
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
                all_pnls.append(pnl)

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]

    if not up.empty:
        ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
        ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
        ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")

    if not down.empty:
        ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
        ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
        ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    try:
        os.makedirs(save_path, exist_ok=True)
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
        print(f"Chart saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}.png')}")
        plt.close(fig)

    except Exception as e:
        print(f"Error saving chart: {e}")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    try:
        os.makedirs(save_path, exist_ok=True)
        plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
        print(f"PNL curve saved to: {os.path.join(save_path, f'{scrip_symbol}_{timeframe}_pnl_curve.png')}")
        plt.close()

    except Exception as e:
        print(f"Error saving PNL curve: {e}")

##Resampling data

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with
    Indian market hours (9:15 - 15:30), ensuring accurate candle
    starting times.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    # Ensure datetime index is in IST timezone
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter for Market Hours
    df = df.between_time('9:15', '15:30')

    # Create a fixed range of time intervals for alignment
    start_time = datetime.time(9, 15)
    end_time = datetime.time(15, 30)

    # Align the index to create consistent candles
    df['aligned_time'] = df.index.map(lambda x: x.replace(second=0, microsecond=0))
    timeframe_minutes = pd.Timedelta(timeframe)

    def align_to_interval(ts):
        # Align timestamp to nearest timeframe
        offset = ((ts.minute - start_time.minute) % timeframe_minutes.seconds // 60)
        return ts - pd.Timedelta(minutes=offset)

    df['aligned_time'] = df['aligned_time'].apply(align_to_interval)
    df.set_index('aligned_time', inplace=True)

    # Resample the data based on aligned index
    resampled_df = df.resample(timeframe).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    }).dropna()

    # Drop extra candles outside market hours
    resampled_df = resampled_df.between_time('9:15', '15:30')

    return resampled_df



def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
       A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df, timeframe)

    signals = gann_strategy(resampled_df, timeframe)

    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    print("Long Trades:")
    for trade in long_trades[:5]:
        print(trade)

    print("\nShort Trades:")
    for trade in short_trades[:5]:
        print(trade)

    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)
        trade['cumulative_profit'] = cumulative_profit

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        os.makedirs(save_path, exist_ok=True)

        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---

stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000
risk_percentage = 1

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://471e62e11fbbbce698.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-29-5b7687afb360>:359: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['aligned_time'] = df.index.map(lambda x: x.replace(second=0, microsecond=0))
<ipython-input-29-5b7687afb360>:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['aligned_time'] = df['aligned_time'].apply(align_to_interval)
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://471e62e11fbbbce698.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.2 (Candle Fix)      ####
# Strategy Name: Gann Square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr


# Gann Square of 9 calculations
def gann_square_of_9(price):
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values


def find_buy_sell_levels(price, gann_values):
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below


def calculate_targets(entry_level, gann_values, direction='long'):
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets


# Gann Strategy
def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    explicitly handling the 9:15 AM candle.
    """
    signals = []
    price_tolerance = 0.01

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_time = price_data.index[i].time()
        previous_date = price_data.index[i - 1].date()

        if current_time == datetime.time(9, 15):
            try:
                previous_price = price_data['close'].loc[previous_date]
            except KeyError:
                continue
        else:
            previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above - price_tolerance:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below + price_tolerance:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target - price_tolerance:
                    closest_timestamp = price_data.index.asof(price_data.index[i])
                    signals.append(('exit_buy', target, j + 1, closest_timestamp))

        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target + price_tolerance:
                    closest_timestamp = price_data.index.asof(price_data.index[i])
                    signals.append(('exit_sell', target, j + 1, closest_timestamp))

    return signals


# Risk management
def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        try:
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
                all_pnls.append(pnl)

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    return metrics, long_trades, short_trades, all_pnls


def resample_data(df, timeframe):
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30').copy()

    timeframe_minutes = pd.Timedelta(timeframe)

    def align_to_interval(ts):
        offset = ((ts.minute % timeframe_minutes.seconds // 60) - 15) % timeframe_minutes.seconds // 60
        return ts - pd.Timedelta(minutes=offset)

    df['aligned_time'] = df.index.map(align_to_interval)
    df = df.set_index('aligned_time')

    resampled_df = df.resample(timeframe).agg({
        'open': 'first',
        'high': 'max',
        'low': 'min',
        'close': 'last',
        'volume': 'sum'
    }).dropna()

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")

    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df, timeframe)
    signals = gann_strategy(resampled_df, timeframe)

    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    return metrics, long_trades, short_trades


# Gradio Interface
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1h'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.JSON(label="Metrics"),
        gr.JSON(label="Long Trades"),
        gr.JSON(label="Short Trades")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://d062414ca7c3cfb16a.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://d062414ca7c3cfb16a.gradio.live


In [ ]:
#Is this code updated for resampling issues for 30 mins and 60 mins ?

####################################
# Author: Mahesh Naidu D        ####
# Version: 1.0                  ####
# Strategy Name: Gann square 9  ####
####################################
import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.
    Args:
      price: The price to calculate Gann values for.
    Returns:
      A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN
    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)
    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places
    return gann_values
def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.
    Args:
      price: The current price.
      gann_values: A list of Gann Square of 9 values.
    Returns:
      A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break
    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None
    return buy_above, sell_below
def calculate_targets(entry_level, gann_values):
    """
    Calculates target levels from an entry level using Gann values.
    Args:
      entry_level: The entry level (buy_above or sell_below).
      gann_values: A list of Gann Square of 9 values.
    Returns:
      A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        targets = gann_values[start_index + 1 : start_index + 5]  # Get next 4 levels
    except ValueError:
        # Handle cases where entry_level is not found in gann_values
        pass
    return targets
def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    Args:
      price_data: A pandas DataFrame with 'close' price data and a datetime index.
      timeframe: The timeframe of the price data (e.g., '5min', '15min', '30min', '1H').
    Returns:
      A list of signals ('buy', 'sell', 'exit') and target levels.
    """
    signals = []
    for i in range(1, len(price_data)):
        current_price = price_data['close'][i]
        previous_price = price_data['close'][i - 1]
        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)
        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values)
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))  # Add timestamp
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values)
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))  # Add timestamp
        # Basicexit conditions (needs further refinement for retracement and timeframe)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))
    return signals
def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.
    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.
    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down to the nearest whole number
    return quantity
def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.
    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.
    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity
    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        if signal == 'buy' and position == 0:
            position = 1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity  # Store the quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal == 'sell' and position == 0:
            position = -1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity  # Store the quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
            all_pnls.append(pnl)  # Add PnL to the list
            if position == 1:
                long_trades[-1]['exit_time'] = timestamp
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = timestamp
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)
            position = 0
    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']
    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0
    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0
    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0
    return metrics, long_trades, short_trades, all_pnls
def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.
    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))
    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")
    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity in the loop
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')
    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()
    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory
def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")
    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
# --- Gradio Interface ---
import gradio as gr
#import os
#import pandas as pd
#import matplotlib.pyplot as plt
#import gradio as gr
def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.
    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.
    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)
    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")
    # Read the Parquet file
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)
    market_start, market_end = '09:15', '15:30'  # Adjusted end time
# --- Resampling with NSE Market Adjustments ---
    if timeframe == '30min':
    # Resample to 30 minutes, aligning with market open
      resampled_df = df.between_time(market_start, market_end).resample('30min', origin='start').agg(
        {'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'}
      )
    elif timeframe == '1H':
    # Resample to 1 hour, aligning with market open
      resampled_df = df.between_time(market_start, market_end).resample('1H', origin='start').agg(
        {'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'}
      )
    else:
    # Standard resampling for other timeframes
      resampled_df = df.resample(timeframe).agg({'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'})
    # --- Gann strategy application ---
    signals = gann_strategy(resampled_df, timeframe)
    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss: 2% below entry
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss: 2% above entry
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))  # No quantity for exit signals
    signals = updated_signals
    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}
    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade['pnl']
        trade['cumulative_profit'] = cumulative_profit
    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)
    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)
    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path
# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]
# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade
# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),  # Use type="filepath"
        gr.Image(label="PNL Curve", type="filepath")        # Use type="filepath"
    ],
    title="Gann Strategy Backtesting"
)
iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://0c24de345a3b94e380.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-13-89bd2f8dbe95>:293: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  resampled_df = df.between_time(market_start, market_end).resample('1H', origin='start').agg(
<ipython-input-13-89bd2f8dbe95>:83: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
<ipython-input-13-89bd2f8dbe95>:84: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = price_data['close'][i - 1]
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = 

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://0c24de345a3b94e380.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.2 (Corrected)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []
    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)
    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break
    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values):
    """
    Calculates target levels from an entry level using Gann values.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        targets = gann_values[start_index + 1 : start_index + 5]
    except ValueError:
        pass
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.

    Args:
        price_data: A pandas DataFrame with 'close' price data and a datetime index.
        timeframe: The timeframe of the price data (e.g., '5min', '15min', '30min', '1H').

    Returns:
        A list of signals ('buy', 'sell', 'exit') and target levels.
    """
    signals = []
    for i in range(1, len(price_data)):
        current_price = price_data['close'][i]
        previous_price = price_data['close'][i - 1]
        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)
        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values)
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values)
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []
    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy' and position == 0:
            position = 1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal == 'sell' and position == 0:
            position = -1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
            all_pnls.append(pnl)
            if position == 1:
                long_trades[-1]['exit_time'] = timestamp
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = timestamp
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)
            position = 0
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']
    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0
    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0
    return metrics, long_trades, short_trades, all_pnls

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')
    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)

def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with
    Indian market hours (9:15 - 15:30), ensuring accurate candle
    starting times.

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """

    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60

    resampled_data = []

    current_time = df.index[0].replace(hour=9, minute=15, second=0, microsecond=0)
    end_time = df.index[-1].replace(hour=15, minute=30, second=0, microsecond=0)  # Set end_time to 3:30 PM

    while current_time <= end_time:  # Correct the loop condition
        next_time = current_time + pd.Timedelta(minutes=timeframe_minutes)
        candle_data = df[(df.index >= current_time) & (df.index < next_time)]

        if not candle_data.empty:
            resampled_data.append({
                'date': current_time,
                'open': candle_data['open'].iloc[0],
                'high': candle_data['high'].max(),
                'low': candle_data['low'].min(),
                'close': candle_data['close'].iloc[-1],
                'volume': candle_data['volume'].sum()
            })

        current_time = next_time

    resampled_df = pd.DataFrame(resampled_data)
    resampled_df.set_index('datetime', inplace=True)

    return resampled_df


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)
    resampled_df = resample_data(df, timeframe)  # Use the corrected resample_data function
    signals = gann_strategy(resampled_df, timeframe)
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))
    signals = updated_signals
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade['pnl']
        trade['cumulative_profit'] = cumulative_profit
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path

# --- Main Execution ---
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]
capital = 100000
risk_percentage = 1
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)
iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://bce8df67b3ea85f625.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://bce8df67b3ea85f625.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.5 (Gann Logic Fixed) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets
##Gann strategy which is generating signals

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for tick_timestamp, tick_price in zip(candle_tick_data.index, candle_tick_data['close']):  # Use 'close' column
            # Calculate Gann levels for each 1-minute candle
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    position = 1
                    signals.append(('buy', entry_price, targets, entry_time))
                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    position = -1
                    signals.append(('sell', entry_price, targets, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if tick_price >= target:
                            signals.append(('exit_buy', tick_price, j+1, tick_timestamp))
                            position = 0
                            break
                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if tick_price <= target:
                            signals.append(('exit_sell', tick_price, j+1, tick_timestamp))
                            position = 0
                            break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


#def resample_data(df, timeframe):
#    """
import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    # ... in your analyze_stock function ...

    resampled_df = resample_data(df, timeframe)

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes)  # Pass resampled_df twice

# ... (rest of your code) ...

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://9b4e16a7f32ea85da2.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-22-91e652f20f29>:374: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-22-91e652f20f29>:374: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-22-91e652f20f29>:116: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-17-906a750a7778>:99: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser

In [ ]:
pip install gradio

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.3 (Multi-level Exits) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals (including partial exits).

    Args:
        signals: A list of signals generated by the gann_strategy_with_tick_data function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal in signals:
        if signal[0] == 'buy' and position == 0:
            position = 1
            entry_price = signal[1]
            entry_time = signal[5]  # Assuming entry_time is the 6th element in the signal
            entry_quantity = signal[4]  # Assuming total_quantity is the 5th element in the signal
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})  # Assuming targets is the 3rd element
        elif signal[0] == 'sell' and position == 0:
            position = -1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0].startswith('exit') and position != 0:
            exit_price = signal[1]
            exit_time = signal[3]  # Assuming exit_time is the 4th element
            exit_quantity = signal[4]  # Assuming exit_quantity is the 5th element
            pnl = (exit_price - entry_price) * exit_quantity if position == 1 else (entry_price - exit_price) * exit_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1]['exit_time'] = exit_time
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl  # Assuming pnl is calculated for the partial exit
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = exit_time
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            # If this is the final exit for the trade, reset position
            if signal[2] == 0:  # Assuming target level 0 indicates final exit (e.g., stop-loss or last target)
                position = 0

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick   Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    # ... in your analyze_stock function ...

    resampled_df = resample_data(df, timeframe)

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes)  # Pass resampled_df twice

# ... (rest of your code) ...

   # ... inside analyze_stock function ...

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)  # Pass capital and risk_percentage

# ... rest of the analyze_stock function ...

    # Modify signals to include quantity
    updated_signals = []
    for signal, entry_level, targets, timestamp in signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://67c46311a63fd82e8e.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-7-151757be573c>:414: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-7-151757be573c>:414: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.4 (Corrected Call)   ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    # Initialize short_wins here
    short_wins = 0
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with   Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://159a8bfe65e4ef9397.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-4-dc2b8c58e551>:415: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-4-dc2b8c58e551>:415: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-4-dc2b8c58e551>:139: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-4-dc2b8c58e551>:146: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.il

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://159a8bfe65e4ef9397.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.6 (Complete Code)    ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals (including partial exits).

    Args:
        signals: A list of signals generated by the gann_strategy_with_tick_data function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal in signals:  # No need to unpack here
        if signal[0] == 'buy' and position == 0:
            position = 1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0] == 'sell' and position == 0:
            position = -1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0].startswith('exit') and position != 0:
            exit_price = signal[1]
            exit_time = signal[3]
            exit_quantity = signal[4]  # Assuming exit_quantity is the 5th element
            pnl = (exit_price - entry_price) * exit_quantity if position == 1 else (entry_price - exit_price) * exit_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1]['exit_time'] = exit_time
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl  # Assuming pnl is calculated for the partial exit
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = exit_time
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            # If this is the final exit for the trade, reset position
            if signal[2] == 0:  # Assuming target level 0 indicates final exit (e.g., stop-loss or last target)
                position = 0

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    # Initialize short_wins here
    short_wins = 0
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)  # Pass capital and risk_percentage

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://87c5f80cac8f0eba6d.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-5-eefbc7b4aeb3>:416: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-5-eefbc7b4aeb3>:416: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-5-eefbc7b4aeb3>:139: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-5-eefbc7b4aeb3>:146: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.il

Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_1H_trades.csv
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://87c5f80cac8f0eba6d.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (Refined & Consistent) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0: # Prevent division by zero if stop_loss_price equals entry_price
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals (including partial exits).

    Args:
        signals: A list of signals generated by the gann_strategy_with_tick_data function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal in signals:  # No need to unpack here
        if signal[0] == 'buy' and position == 0:
            position = 1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0] == 'sell' and position == 0:
            position = -1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0].startswith('exit') and position != 0:
            exit_price = signal[1]
            exit_time = signal[3]
            exit_quantity = signal[4]  # Assuming exit_quantity is the 5th element
            pnl = (exit_price - entry_price) * exit_quantity if position == 1 else (entry_price - exit_price) * exit_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1]['exit_time'] = exit_time
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl  # Assuming pnl is calculated for the partial exit
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = exit_time
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            # If this is the final exit for the trade, reset position
            if signal[2] == 0:  # Assuming target level 0 indicates final exit (e.g., stop-loss or last target)
                position = 0

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    # Initialize short_wins here
    short_wins = 0
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)  # Pass capital and risk_percentage

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://aeab838b514846f8a0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-6-af597bf8128c>:418: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-6-af597bf8128c>:418: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-6-af597bf8128c>:141: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-6-af597bf8128c>:148: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.il

Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_1H_trades.csv
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://aeab838b514846f8a0.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (Refined & Consistent) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0: # Prevent division by zero if stop_loss_price equals entry_price
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals (including partial exits).

    Args:
        signals: A list of signals generated by the gann_strategy_with_tick_data function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity
    remaining_quantity = 0  # Track remaining quantity for partial exits

    for signal in signals:  # No need to unpack here
        if signal[0] == 'buy' and position == 0:
            position = 1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            remaining_quantity = entry_quantity  # Initialize remaining quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0] == 'sell' and position == 0:
            position = -1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            remaining_quantity = entry_quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0].startswith('exit') and position != 0:
            exit_price = signal[1]
            exit_time = signal[3]
            exit_quantity = signal[4]
            pnl = (exit_price - entry_price) * exit_quantity if position == 1 else (entry_price - exit_price) * exit_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1].setdefault('exit_time', exit_time)  # Use setdefault to avoid overwriting
                long_trades[-1].setdefault('exit_price', exit_price)
                long_trades[-1].setdefault('pnl', 0)  # Initialize pnl if not already present
                long_trades[-1]['pnl'] += pnl  # Add to existing pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1].setdefault('exit_time', exit_time)
                short_trades[-1].setdefault('exit_price', exit_price)
                short_trades[-1].setdefault('pnl', 0)
                short_trades[-1]['pnl'] += pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            remaining_quantity -= exit_quantity
            if remaining_quantity == 0:  # Check if this was the final exit
                position = 0

    # ... (rest of the metrics calculation remains the same)


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of       the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://228f164db8ad448d03.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-7-ea6c2b52bfdb>:387: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-7-ea6c2b52bfdb>:387: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-7-ea6c2b52bfdb>:141: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-7-ea6c2b52bfdb>:148: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.il

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://228f164db8ad448d03.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (Refined & Consistent) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass
    return targets

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0: # Prevent division by zero if stop_loss_price equals entry_price
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes, capital, risk_percentage):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle and uses multi-level exits with partial profit taking.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.
        capital (float): Trading capital.
        risk_percentage (float): Risk percentage per trade.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []
    stop_loss = None
    total_quantity = 0
    remaining_quantity = 0
    exit_percentages = [0.25, 0.50, 0.25]  # Example: 25% at each target

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for k in range(len(candle_tick_data)):
            tick_timestamp = candle_tick_data.index[k]
            tick_price = candle_tick_data['close'][k]
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    stop_loss = entry_price * 0.98  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = 1
                    signals.append(('buy', entry_price, targets, stop_loss, total_quantity, entry_time))

                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    stop_loss = entry_price * 1.02  # Example: 2% stop-loss
                    total_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss)
                    remaining_quantity = total_quantity
                    position = -1
                    signals.append(('sell', entry_price, targets, stop_loss, total_quantity, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price >= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_buy', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price <= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 0, tick_timestamp, exit_quantity))  # Target 0 for stop-loss

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and buy_above and tick_price >= buy_above:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]  # Exit at the first target
                        remaining_quantity = 0
                        signals.append(('exit_buy', exit_price, 1, tick_timestamp, exit_quantity))  # Target 1 for dynamic exit

                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if remaining_quantity > 0 and tick_price <= target:
                            exit_quantity = total_quantity * exit_percentages[j]
                            exit_price = target
                            remaining_quantity -= exit_quantity
                            signals.append(('exit_sell', exit_price, j+1, tick_timestamp, exit_quantity))

                    # Check for stop-loss
                    if remaining_quantity > 0 and tick_price >= stop_loss:
                        exit_quantity = remaining_quantity
                        exit_price = stop_loss
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 0, tick_timestamp, exit_quantity))

                    # Dynamic exit at Target 1 if a new signal occurs (simplified for now)
                    if remaining_quantity > 0 and sell_below and tick_price <= sell_below:
                        exit_quantity = remaining_quantity
                        exit_price = targets[0]
                        remaining_quantity = 0
                        signals.append(('exit_sell', exit_price, 1, tick_timestamp, exit_quantity))

    return signals

#def calculate_metrics(signals, price_data):
def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals (including partial exits).

    Args:
        signals: A list of signals generated by the gann_strategy_with_tick_data function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity
    remaining_quantity = 0  # Track remaining quantity for partial exits

    for signal in signals:
        if signal[0] == 'buy' and position == 0:
            position = 1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            remaining_quantity = entry_quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0] == 'sell' and position == 0:
            position = -1
            entry_price = signal[1]
            entry_time = signal[5]
            entry_quantity = signal[4]
            remaining_quantity = entry_quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': signal[2], 'quantity': entry_quantity})
        elif signal[0].startswith('exit') and position != 0:
            exit_price = signal[1]
            exit_time = signal[3]
            exit_quantity = signal[4]
            pnl = (exit_price - entry_price) * exit_quantity if position == 1 else (entry_price - exit_price) * exit_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1].setdefault('exit_time', exit_time)
                long_trades[-1].setdefault('exit_price', exit_price)
                long_trades[-1].setdefault('pnl', 0)
                long_trades[-1]['pnl'] += pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1].setdefault('exit_time', exit_time)
                short_trades[-1].setdefault('exit_price', exit_price)
                short_trades[-1].setdefault('pnl', 0)
                short_trades[-1]['pnl'] += pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            remaining_quantity -= exit_quantity
            if remaining_quantity == 0:
                position = 0

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    short_wins = 0  # Initialize short_wins
    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal in signals:
        if signal[0] == 'buy':
            ax.plot(signal[5], signal[1], '^', markersize=10, color='g', label='Buy')
        elif signal[0] == 'sell':
            ax.plot(signal[5], signal[1], 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Apply Gann strategy
    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes, capital, risk_percentage)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    try:
        # Ensure the directory exists
        os.makedirs(save_path, exist_ok=True)

        # Save results
        metrics_df = pd.DataFrame(all_metrics).transpose()
        metrics_df.to_csv(metrics_path, index=False)
        print(f"Metrics saved to: {metrics_path}")

        long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
        short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
        long_trades_df['trade_type'] = 'long'
        short_trades_df['trade_type'] = 'short'
        all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
        all_trades_df.to_csv(trades_path, index=False)
        print(f"Trades saved to: {trades_path}")

    except Exception as e:
        print(f"Error saving results: {e}")

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f5a175d97c49500dd7.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-10-829865b51d6a>:423: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-10-829865b51d6a>:423: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-10-829865b51d6a>:141: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
<ipython-input-10-829865b51d6a>:148: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `se

Metrics saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_metrics.csv
Trades saved to: /content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data/Gann_Charts/SIEMEN/SIEMEN_1H_trades.csv
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://f5a175d97c49500dd7.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D           ####
# Version: 1.6 (ML Integrated)    ####
# Strategy Name: Gann square 9     ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime

# --- Gann Square Calculations ---

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets


# --- Gann Strategy with Tick Data ---

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for tick_timestamp, tick_price in zip(candle_tick_data.index, candle_tick_data['close']):
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    stop_loss_price = buy_above * 0.98  # Example stop-loss
                    quantity = calculate_quantity(capital, tick_price, risk_percentage, stop_loss_price)
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    position = 1
                    signals.append(('buy', tick_price, targets, tick_timestamp, quantity, stop_loss_price))
                elif sell_below and tick_price <= sell_below:
                    stop_loss_price = sell_below * 1.02  # Example stop-loss
                    quantity = calculate_quantity(capital, tick_price, risk_percentage, stop_loss_price)
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    position = -1
                    signals.append(('sell', tick_price, targets, tick_timestamp, quantity, stop_loss_price))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if tick_price >= target:
                            signals.append(('exit_buy', tick_price, j+1, tick_timestamp))
                            position = 0
                            break
                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if tick_price <= target:
                            signals.append(('exit_sell', tick_price, j+1, tick_timestamp))
                            position = 0
                            break

    return signals


# --- Quantity and Risk Management ---

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


# --- Performance Metrics ---

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity, stop_loss_price in signals:  # Include quantity and stop_loss_price
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity, 'stop_loss_price': stop_loss_price})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity, 'stop_loss_price': stop_loss_price})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


# --- Charting ---

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity, stop_loss_price in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


# --- Data Resampling ---

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


# --- Technical Indicators ---

def calculate_rsi(prices, period=14):
    """
    Calculates the Relative Strength Index (RSI) for a given price series.

    Args:
        prices (pd.Series): A pandas Series of prices.
        period (int): The lookback period for RSI calculation.

    Returns:
        pd.Series: A pandas Series with RSI values.
    """
    deltas = prices.diff()
    gain = deltas.where(deltas > 0, 0.0)
    loss = -deltas.where(deltas < 0, 0.0)

    avg_gain = gain.rolling(window=period).mean()
    avg_loss = loss.rolling(window=period).mean()

    rs = avg_gain / avg_loss
    rsi = 100 - (100 / (1 + rs))

    return rsi


# --- Feature Engineering ---

def create_features(df):
    """
    Generates features for the ML model.

    Args:
        df (pd.DataFrame): DataFrame with OHLCV data and Gann levels.

    Returns:
        pd.DataFrame: DataFrame with added features.
    """
    # Calculate Gann levels
    gann_values_list = df['close'].apply(gann_square_of_9)
    df['gann_values'] = gann_values_list

    # You'll need to adjust this part based on how you want to use Gann values as features
    df['buy_above'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[0], axis=1)
    df['sell_below'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[1], axis=1)

    # Calculate other features
    df['distance_to_buy_above'] = df['buy_above'] - df['close']
    df['distance_to_sell_below'] = df['close'] - df['sell_below']
    df['SMA_50'] = df['close'].rolling(window=50).mean()
    df['RSI'] = calculate_rsi(df['close'])
    # ... add more features (MACD, volume indicators, etc.) ...

    return df


# --- Machine Learning Model ---

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

def train_model(df):
    """
    Trains a Random Forest classifier to predict signals.

    Args:
        df (pd.DataFrame): DataFrame with features and target variable.

    Returns:
        sklearn.ensemble.RandomForestClassifier: Trained Random Forest model.
    """
    # Add a 'signal' column based on price crossover with Gann levels
    df['signal'] = 0  # Initialize
    df.loc[df['close'] > df['buy_above'], 'signal'] = 1  # Buy signal
    df.loc[df['close'] < df['sell_below'], 'signal'] = -1  # Sell signal

    # Prepare data
    X = df[['distance_to_buy_above', 'distance_to_sell_below', 'SMA_50', 'RSI']]
    y = df['signal']
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train the model
    model = RandomForestClassifier(n_estimators=100, random_state=42)
    model.fit(X_train, y_train)

    return model


# --- Main Analysis Function ---

def analyze_stock(stock_name, timeframe='5min', capital=100000, risk_percentage=1):
    """
    Analyzes the selected stock and timeframe using the Gann strategy with ML integration.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.
        capital: The initial trading capital.
        risk_percentage: The percentage of capital to risk per trade.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "stock_min_data"  # Update with your actual data directory
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")  # Assuming parquet format
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60

    # Generate Gann signals with quantity and stop-loss
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes)

    # Create features
    df_with_features = create_features(resampled_df.copy())

    # Train ML model
    model = train_model(df_with_features)

    # Make predictions
    predictions = model.predict(df_with_features[['distance_to_buy_above', 'distance_to_sell_below', 'SMA_50', 'RSI']])

    # Integrate predictions into your strategy (example: filter signals)
    filtered_signals = []
    for i, signal in enumerate(signals):
        if int(predictions[i]) == 1 and signal[0] == 'buy':  # Buy signal
            filtered_signals.append(signal)
        elif int(predictions[i]) == -1 and signal[0] == 'sell':  # Sell signal
            filtered_signals.append(signal)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(filtered_signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, filtered_signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution (Example Usage) ---

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Example usage with a sample stock name and timeframe
stock_name = "sample_stock"  # Replace with your actual stock name
timeframe = "5min"
metrics_df, trades_df, chart_path, pnl_path = analyze_stock(stock_name, timeframe, capital, risk_percentage)

print("Metrics:")
print(metrics_df)
print("\nTrades:")
print(trades_df)
print(f"\nChart saved to: {chart_path}")
print(f"PNL curve saved to: {pnl_path}")

FileNotFoundError: [Errno 2] No such file or directory: 'stock_min_data/sample_stock/sample_stock.parquet'

In [ ]:
####################################
# Author: Mahesh Naidu D           ####
# Version: 2.1 (ML Integrated)    ####
# Strategy Name: Gann square 9     ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

# --- Gann Square Calculations ---

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

# --- Gann Strategy with Tick Data ---

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for tick_timestamp, tick_price in zip(candle_tick_data.index, candle_tick_data['close']):
            # Calculate Gann levels for each 1-minute candle
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    position = 1
                    signals.append(('buy', entry_price, targets, entry_time))
                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    position = -1
                    signals.append(('sell', entry_price, targets, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if tick_price >= target:
                            signals.append(('exit_buy', tick_price, j+1, tick_timestamp))
                            position = 0
                            break
                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if tick_price <= target:
                            signals.append(('exit_sell', tick_price, j+1, tick_timestamp))
                            position = 0
                            break

    return signals

# --- Quantity and Risk Management ---

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity

# --- Performance Metrics ---

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Initialize long_wins and short_wins here
    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls

# --- Charting ---

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

# --- Data Resampling ---

import pandas as pd

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

# --- Feature Engineering ---

def create_features(df):
    """
    Generates features for the ML model.
    """
    # Calculate Gann levels
    gann_values_list = df['close'].apply(gann_square_of_9)
    df['gann_values'] = gann_values_list
    df['buy_above'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[0], axis=1)
    df['sell_below'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[1], axis=1)

    # Calculate features
    df['is_above_gann_level'] = (df['close'] > df['buy_above']).astype(int)
    df['is_below_gann_level'] = (df['close'] < df['sell_below']).astype(int)

    # ... (Add calculations for nearest_gann_level, gann_level_trend,
    #      price_momentum, price_volatility, etc.) ...

    return df

# --- Machine Learning Model ---

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

def train_model(df):
    """
    Trains a Random Forest classifier to predict signals.
    """
    # Add a 'signal' column based on price crossover with Gann levels
    df['signal'] = 0
    df.loc[df['close'] > df['buy_above'], 'signal'] = 1  # Buy signal
    df.loc[df['close'] < df['sell_below'], 'signal'] = -1  # Sell signal

    # Prepare data
    X = df[['distance_to_buy_above', 'distance_to_sell_below', 'SMA_50']]
    y = df['signal']
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train the model
    model = RandomForestClassifier(n_estimators=100, random_state=42)
    model.fit(X_train, y_train)
    return model

# --- Main Analysis Function ---

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60

    # Generate Gann signals
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes)

    # --- ML Integration ---
    # Create features
    df_with_features = create_features(resampled_df.copy())

    # Train ML model
    model = train_model(df_with_features)

    # Make predictions (no RSI in features)
    predictions = model.predict(df_with_features[['distance_to_buy_above', 'distance_to_sell_below', 'SMA_50']])

    # Integrate predictions into your strategy (filter signals)
    filtered_signals = []
    for i, signal in enumerate(signals):
        if int(predictions[i]) == 1 and signal[0] == 'buy':  # Buy signal
            filtered_signals.append(signal)
        elif int(predictions[i]) == -1 and signal[0] == 'sell':  # Sell signal
            filtered_signals.append(signal)

    # --- End of ML Integration ---

    # Modify signals to include quantity (using filtered_signals now)
    updated_signals = []
    for signal, entry_level, targets, timestamp in filtered_signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals  # Update the signals variable

    # Calculate metrics (using updated_signals)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://2d7d23e63a9ba3e49e.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-5-11c5224a7a37>:383: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-5-11c5224a7a37>:383: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-5-11c5224a7a37>:119: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://2d7d23e63a9ba3e49e.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D           ####
# Version: 2.4 (ML Integrated)    ####
# Strategy Name: Gann square 9     ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

# --- Gann Square Calculations ---

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]  # Reverse for short
    except ValueError:
        pass
    return targets

# --- Gann Strategy with Tick Data ---

def gann_strategy_with_tick_data(resampled_df, tick_data, timeframe_minutes):
    """
    Implements the Gann strategy with 1-minute data for precise entry and exit.
    Calculates Gann levels for each 1-minute candle.

    Args:
        resampled_df (pd.DataFrame): DataFrame with resampled candle data.
        tick_data (pd.DataFrame): DataFrame with 1-minute data (datetime index, 'close' column).
        timeframe_minutes (int): Timeframe in minutes.

    Returns:
        list: List of signals with 1-minute level entry and exit points.
    """

    signals = []
    position = 0  # 0 for no position, 1 for long, -1 for short
    entry_price = 0
    entry_time = None
    targets = []

    for i in range(1, len(resampled_df)):
        current_candle_start = resampled_df.index[i]
        current_candle_end = resampled_df.index[i] + pd.Timedelta(minutes=timeframe_minutes)
        previous_price = resampled_df['close'][i - 1]

        # Extract 1-minute data for the current candle
        candle_tick_data = tick_data[(tick_data.index >= current_candle_start) & (tick_data.index < current_candle_end)]

        for tick_timestamp, tick_price in zip(candle_tick_data.index, candle_tick_data['close']):
            # Calculate Gann levels for each 1-minute candle
            gann_values = gann_square_of_9(previous_price)
            buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

            if not position:  # Not in a position
                if buy_above and tick_price >= buy_above:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(buy_above, gann_values, direction='long')
                    position = 1
                    signals.append(('buy', entry_price, targets, entry_time))
                elif sell_below and tick_price <= sell_below:
                    entry_price = tick_price
                    entry_time = tick_timestamp
                    targets = calculate_targets(sell_below, gann_values, direction='short')
                    position = -1
                    signals.append(('sell', entry_price, targets, entry_time))

            else:  # In a position
                if position == 1:  # Long position
                    for j, target in enumerate(targets):
                        if tick_price >= target:
                            signals.append(('exit_buy', tick_price, j+1, tick_timestamp))
                            position = 0
                            break
                elif position == -1:  # Short position
                    for j, target in enumerate(targets):
                        if tick_price <= target:
                            signals.append(('exit_sell', tick_price, j+1, tick_timestamp))
                            position = 0
                            break

    return signals

# --- Quantity and Risk Management ---

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity

# --- Performance Metrics ---

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls

# --- Charting ---

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()

# --- Data Resampling ---

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

# --- Feature Engineering ---

def create_features(df):
    """
    Generates features for the ML model.
    """
    # Calculate Gann levels and identify nearest level
    df['gann_values'] = df['close'].apply(gann_square_of_9)
    df['buy_above'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[0], axis=1)
    df['sell_below'] = df.apply(lambda row: find_buy_sell_levels(row['close'], row['gann_values'])[1], axis=1)

    # New features based on Gann levels and targets
    df['is_above_gann_level'] = (df['close'] > df['buy_above']).astype(int)
    df['is_below_gann_level'] = (df['close'] < df['sell_below']).astype(int)
    df['nearest_gann_level'] = np.where(df['is_above_gann_level'], df['buy_above'], df['sell_below'])
    df['distance_to_nearest_gann_level'] = abs(df['close'] - df['nearest_gann_level'])

    # ... (Add calculations for gann_level_trend, price_momentum, price_volatility, etc.) ...

    return df

# --- Machine Learning Model ---

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

def train_model(df):
    """
    Trains a Random Forest classifier to predict signals.
    """
    # Add a 'signal' column based on price crossover with Gann levels
    df['signal'] = 0
    df.loc[df['close'] > df['buy_above'], 'signal'] = 1  # Buy signal
    df.loc[df['close'] < df['sell_below'], 'signal'] = -1  # Sell signal

    # Prepare data (use the new features)
    X = df[['is_above_gann_level', 'is_below_gann_level', 'distance_to_nearest_gann_level']]  # Example features
    y = df['signal']
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train the model
    model = RandomForestClassifier(n_estimators=100, random_state=42)
    model.fit(X_train, y_train)
    return model

# --- Main Analysis Function ---

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    timeframe_minutes = int(timeframe[:-3]) if timeframe.endswith('min') else 60

    # Generate Gann signals
    signals = gann_strategy_with_tick_data(resampled_df, resampled_df, timeframe_minutes)

    # --- ML Integration ---
    # Create features
    df_with_features = create_features(resampled_df.copy())

    # Train ML model
    model = train_model(df_with_features)

    # Make predictions
    predictions = model.predict(df_with_features[['is_above_gann_level', 'is_below_gann_level', 'distance_to_nearest_gann_level']])

    # Integrate predictions into your strategy (filter signals)
    filtered_signals = []
    for i, signal in enumerate(signals):
        if int(predictions[i]) == 1 and signal[0] == 'buy':  # Buy signal
            filtered_signals.append(signal)
        elif int(predictions[i]) == -1 and signal[0] == 'sell':  # Sell signal
            filtered_signals.append(signal)

    # --- End of ML Integration ---

    # Modify signals to include quantity (using filtered_signals now)
    updated_signals = []
    for signal, entry_level, targets, timestamp in filtered_signals:
        if signal == 'buy':
            stop_loss_price = entry_level * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('buy', entry_level, targets, timestamp, quantity))
        elif signal == 'sell':
            stop_loss_price = entry_level * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_level, risk_percentage, stop_loss_price)
            updated_signals.append(('sell', entry_level, targets, timestamp, quantity))
        else:
            updated_signals.append((signal, entry_level, targets, timestamp, None))

    signals = updated_signals  # Update the signals variable

    # Calculate metrics (using updated_signals)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://a8e4efa2242abfea80.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-6-6f90abc38c0a>:380: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-6-6f90abc38c0a>:380: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-6-6f90abc38c0a>:119: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = resampled_df['close'][i - 1]


New ML development from chatgpt

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.5 (Gann Logic Fixed) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import gradio as gr
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error


# --- Gann Square of 9 Functions ---
def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values


def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below


# --- ML Functions ---
def prepare_ml_data(df):
    """
    Prepares data for ML model using Gann calculations and ATR-based scaling.
    """
    # ATR for scaling
    df['atr'] = df['high'].rolling(5).max() - df['low'].rolling(5).min()

    # Relative distance to Gann levels
    df['dist_to_buy'] = df['buy_above'] - df['close']
    df['dist_to_sell'] = df['close'] - df['sell_below']

    # Targets for ML (dynamic Gann targets)
    df['target1_long'] = df['buy_above'] + (1 * df['atr'])
    df['target2_long'] = df['buy_above'] + (2 * df['atr'])
    df['target3_long'] = df['buy_above'] + (3 * df['atr'])
    df['target1_short'] = df['sell_below'] - (1 * df['atr'])
    df['target2_short'] = df['sell_below'] - (2 * df['atr'])
    df['target3_short'] = df['sell_below'] - (3 * df['atr'])

    return df.dropna()


def train_gann_target_model(df):
    """
    Trains a multi-output regression model to predict multiple Gann targets.
    """
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    targets = ['target1_long', 'target2_long', 'target3_long',
               'target1_short', 'target2_short', 'target3_short']

    # Train-test split
    X = df[features]
    y = df[targets]
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Multi-output regression model
    base_model = RandomForestRegressor(n_estimators=100, random_state=42)
    model = MultiOutputRegressor(base_model)
    model.fit(X_train, y_train)

    # Evaluate model
    predictions = model.predict(X_test)
    print("Mean Absolute Error:", mean_absolute_error(y_test, predictions))
    return model


def predict_gann_targets(model, row):
    """
    Predicts multiple Gann targets for the current row using the trained model.
    """
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    return model.predict(row[features].values.reshape(1, -1))[0]


# --- Metrics Function ---
def calculate_metrics(signals, price_data):
    """
    Updates metrics to incorporate multiple ML-predicted targets.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy' and position == 0:
            position = 1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal == 'sell' and position == 0:
            position = -1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1]['exit_time'] = timestamp
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = timestamp
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            position = 0

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Sharpe and Sortino ratios
    returns = pd.Series(all_pnls)
    metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
    negative_returns = returns[returns < 0]
    metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0

    return metrics, long_trades, short_trades, all_pnls


# --- Analyze Stock Function ---
def analyze_stock(stock_name, timeframe='5min'):
    """
    Updated to integrate ML-predicted targets dynamically.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")

    # Read data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Prepare data for ML
    prepared_df = prepare_ml_data(resampled_df)

    # Train ML model
    model = train_gann_target_model(prepared_df)

    # Predict targets and generate signals
    updated_signals = []
    for i, row in prepared_df.iterrows():
        predicted_targets = predict_gann_targets(model, row)
        if row['close'] >= row['buy_above']:
            updated_signals.append(('buy', row['buy_above'], predicted_targets[:3], i, 0))  # Long targets
        elif row['close'] <= row['sell_below']:
            updated_signals.append(('sell', row['sell_below'], predicted_targets[3:], i, 0))  # Short targets

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(updated_signals, resampled_df)

    # Save results
# Save metrics and trades
    metrics_df = pd.DataFrame(metrics, index=[0])
    long_trades_df = pd.DataFrame(long_trades)
    short_trades_df = pd.DataFrame(short_trades)
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)

    if not os.path.exists(save_path):
        os.makedirs(save_path)
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    # Return results
    return metrics_df, all_trades_df, None, None  # Replace None with plots if needed
# --- Gradio Interface ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Gradio app
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy with ML-Enhanced Targets",
    description="Backtest Gann strategy with dynamically predicted multiple targets using ML integration."
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://8cba4250b819fce0dc.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://8cba4250b819fce0dc.gradio.live


In [ ]:
pip install gradio

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.5 (Gann Logic Fixed) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
import gradio as gr

# --- Gann Square of 9 Functions ---
def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    """
    if math.isnan(price):
        return []  # Return an empty list if price is NaN

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    return gann_values


def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.
    """
    min_positive_index = -1
    for i, value in enumerate(gann_values):
        if value >= price:
            min_positive_index = i
            break

    if min_positive_index >= 0:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below


# --- Resample Data Function ---
def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).
    """
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


# --- ML Functions ---
def prepare_ml_data(df):
    """
    Prepares data for ML model using Gann calculations and ATR-based scaling.
    """
    df['atr'] = df['high'].rolling(5).max() - df['low'].rolling(5).min()
    df['dist_to_buy'] = df['buy_above'] - df['close']
    df['dist_to_sell'] = df['close'] - df['sell_below']

    # Targets for ML (dynamic Gann targets)
    df['target1_long'] = df['buy_above'] + (1 * df['atr'])
    df['target2_long'] = df['buy_above'] + (2 * df['atr'])
    df['target3_long'] = df['buy_above'] + (3 * df['atr'])
    df['target1_short'] = df['sell_below'] - (1 * df['atr'])
    df['target2_short'] = df['sell_below'] - (2 * df['atr'])
    df['target3_short'] = df['sell_below'] - (3 * df['atr'])

    return df.dropna()


def train_gann_target_model(df):
    """
    Trains a multi-output regression model to predict multiple Gann targets.
    """
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    targets = ['target1_long', 'target2_long', 'target3_long',
               'target1_short', 'target2_short', 'target3_short']

    # Train-test split
    X = df[features]
    y = df[targets]
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Multi-output regression model
    base_model = RandomForestRegressor(n_estimators=100, random_state=42)
    model = MultiOutputRegressor(base_model)
    model.fit(X_train, y_train)

    # Evaluate model
    predictions = model.predict(X_test)
    print("Mean Absolute Error:", mean_absolute_error(y_test, predictions))
    return model


def predict_gann_targets(model, row):
    """
    Predicts multiple Gann targets for the current row using the trained model.
    """
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    return model.predict(row[features].values.reshape(1, -1))[0]


# --- Gann Strategy ---
def gann_strategy(price_data, timeframe, model):
    """
    Implements the Gann strategy with ML-predicted targets.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        gann_values = gann_square_of_9(current_price)
        buy_above, sell_below = find_buy_sell_levels(current_price, gann_values)

        current_data = price_data.iloc[i:i+1]
        predicted_targets = predict_gann_targets(model, current_data)

        if current_price >= buy_above:
            buy_targets = predicted_targets[:3]  # First 3 predicted long targets
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif current_price <= sell_below:
            sell_targets = predicted_targets[3:]  # First 3 predicted short targets
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

    return signals


# --- Calculate Quantity ---
def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    quantity = math.floor(risk_amount / risk_per_share)  # Round down
    return quantity


# --- Metrics Function ---
def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on generated signals.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy' and position == 0:
            position = 1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal == 'sell' and position == 0:
            position = -1
            entry_price = entry_level
            entry_time = timestamp
            entry_quantity = quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
            all_pnls.append(pnl)

            if position == 1:
                long_trades[-1]['exit_time'] = timestamp
                long_trades[-1]['exit_price'] = exit_price
                long_trades[-1]['pnl'] = pnl
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
                long_pnl.append(pnl)
            else:
                short_trades[-1]['exit_time'] = timestamp
                short_trades[-1]['exit_price'] = exit_price
                short_trades[-1]['pnl'] = pnl
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
                short_pnl.append(pnl)

            position = 0

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Calculate Sharpe and Sortino ratios
    returns = pd.Series(all_pnls)
    metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
    negative_returns = returns[returns < 0]
    metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0

    return metrics, long_trades, short_trades, all_pnls

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals and saves it to a file.
    """
    fig, ax = plt.subplots(figsize=(12, 6))
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_level, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_level, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)

def analyze_stock(stock_name, timeframe='5min'):
    """
    Integrates ML with Gann strategy for stock analysis.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")

    # Read data
    df = pd.read_parquet(file_path)
    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df, timeframe)

    # Prepare Gann values
    resampled_df['gann_values'] = resampled_df['close'].apply(gann_square_of_9)
    resampled_df['buy_above'], resampled_df['sell_below'] = zip(
        *resampled_df['close'].apply(lambda x: find_buy_sell_levels(x, gann_square_of_9(x)))
    )

    # Prepare data for ML
    prepared_df = prepare_ml_data(resampled_df)

    # Train ML model
    model = train_gann_target_model(prepared_df)

    # Apply Gann strategy
    signals = gann_strategy(prepared_df, timeframe, model)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Save trades and metrics
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    pd.DataFrame(metrics, index=[0]).to_csv(metrics_path, index=False)
    pd.DataFrame(long_trades + short_trades).to_csv(trades_path, index=False)

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Return results
    return metrics, trades_path, metrics_path, save_path

# Get the list of stocks
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Gradio App
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Textbox(label="Trades CSV Path"),
        gr.Textbox(label="Metrics CSV Path"),
        gr.Textbox(label="Save Path")
    ],
    title="Gann Strategy with ML-Enhanced Targets",
    description="Backtest Gann strategy with dynamically predicted multiple targets using ML integration."
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f88b7af969c8ade17a.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-4-81e04962cc75>:76: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-4-81e04962cc75>:76: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({


Mean Absolute Error: 26.126607150537705


Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
<ipython-input-4-81e04962cc75>:147: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not hav

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://f88b7af969c8ade17a.gradio.live


<ipython-input-4-81e04962cc75>:147: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but RandomForestRegressor wa

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.5 (Gann Logic Fixed) ####
# Strategy Name: Gann square 9   ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
import gradio as gr


# --- Gann Square of 9 Functions ---
def gann_square_of_9(price):
    if math.isnan(price):
        return []
    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)
    gann_values = [round((rounded + 0.125 * (i + 1)) ** 2, 2) for i in range(24)]
    return gann_values


def find_buy_sell_levels(price, gann_values):
    min_positive_index = next((i for i, v in enumerate(gann_values) if v >= price), -1)
    buy_above = gann_values[min_positive_index] if min_positive_index >= 0 else None
    sell_below = gann_values[min_positive_index - 1] if min_positive_index >= 0 else None
    return buy_above, sell_below


# --- ML Functions ---
def prepare_ml_data(df):
    df['atr'] = df['high'].rolling(5).max() - df['low'].rolling(5).min()
    df['dist_to_buy'] = df['buy_above'] - df['close']
    df['dist_to_sell'] = df['close'] - df['sell_below']
    df['target1_long'] = df['buy_above'] + (1 * df['atr'])
    df['target2_long'] = df['buy_above'] + (2 * df['atr'])
    df['target3_long'] = df['buy_above'] + (3 * df['atr'])
    df['target1_short'] = df['sell_below'] - (1 * df['atr'])
    df['target2_short'] = df['sell_below'] - (2 * df['atr'])
    df['target3_short'] = df['sell_below'] - (3 * df['atr'])
    return df.dropna()


def train_gann_target_model(df):
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    targets = ['target1_long', 'target2_long', 'target3_long',
               'target1_short', 'target2_short', 'target3_short']
    X, y = df[features], df[targets]
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    model = MultiOutputRegressor(RandomForestRegressor(n_estimators=100, random_state=42)).fit(X_train, y_train)
    print("Mean Absolute Error:", mean_absolute_error(y_test, model.predict(X_test)))
    return model


def predict_gann_targets(model, row):
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    return model.predict(row[features].values.reshape(1, -1))[0]


# --- Gann Strategy ---
def gann_strategy(price_data, timeframe, model):
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        gann_values = gann_square_of_9(current_price)
        buy_above, sell_below = find_buy_sell_levels(current_price, gann_values)
        row = price_data.iloc[i:i + 1]
        predicted_targets = predict_gann_targets(model, row)

        if buy_above and current_price >= buy_above:
            buy_targets = predicted_targets[:3]
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = predicted_targets[3:]
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))
    return signals


# --- Metrics Calculation ---
def calculate_metrics(signals, price_data):
    metrics = defaultdict(int)
    long_trades, short_trades = [], []
    long_pnl, short_pnl, all_pnls = [], [], []
    position = 0
    entry_price, entry_time, entry_quantity = 0, None, 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy' and position == 0:
            position, entry_price, entry_time, entry_quantity = 1, entry_level, timestamp, quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets})
        elif signal == 'sell' and position == 0:
            position, entry_price, entry_time, entry_quantity = -1, entry_level, timestamp, quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
            all_pnls.append(pnl)
            if position == 1:
                long_trades[-1]['pnl'] = pnl
                long_pnl.append(pnl)
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
            else:
                short_trades[-1]['pnl'] = pnl
                short_pnl.append(pnl)
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
            position = 0

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    metrics['winning_trades'] = sum(1 for p in long_pnl + short_pnl if p > 0)
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'], metrics['sortino_ratio'] = 0, 0

    return metrics, long_trades, short_trades, all_pnls


# --- Visualization ---
def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    fig, ax = plt.subplots(figsize=(12, 6))
    up, down = df[df.close >= df.open], df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, color="green")
    ax.bar(down.index, down.close - down.open, color="red")
    for signal, entry_level, targets, timestamp, _ in signals:
        color = 'g' if signal == 'buy' else 'r'
        ax.plot(timestamp, entry_level, 'o', color=color)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close()


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


# --- Resample Data ---
def resample_data(df, timeframe):
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    df = df.between_time('9:15', '15:30')
    resampled = df.resample(timeframe).agg({'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'})
    return resampled.dropna()


# --- Analyze Stock ---
def analyze_stock(stock_name, timeframe='5min'):
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)
    df = pd.read_parquet(os.path.join(stock_path, f"{stock_name}.parquet"))
    df['date'] = pd.to_datetime(df['datetime'])
    df.set_index('date', inplace=True)
    resampled_df = resample_data(df, timeframe)

    # Calculate Gann levels
    resampled_df['buy_above'], resampled_df['sell_below'] = zip(
        *resampled_df['close'].apply(lambda x: find_buy_sell_levels(x, gann_square_of_9(x)))
    )

    # Prepare ML data and train model
    prepared_df = prepare_ml_data(resampled_df)
    model = train_gann_target_model(prepared_df)

    # Generate signals
    signals = gann_strategy(prepared_df, timeframe, model)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Create charts and save
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save metrics and trades
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")

    metrics_df = pd.DataFrame([metrics])
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(long_trades)
    short_trades_df = pd.DataFrame(short_trades)
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Return results
    return metrics_df, trades_path, metrics_path, save_path


# --- Gradio Interface ---
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Textbox(label="Trades CSV Path"),
        gr.Textbox(label="Metrics CSV Path"),
        gr.Textbox(label="Save Path")
    ],
    title="Gann Strategy with ML-Enhanced Targets",
    description="Backtest Gann strategy with dynamically predicted multiple targets using ML integration."
)

iface.launch(debug=True)

In [ ]:
pip install gradio

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 1.6 (Polished)        ####
# Strategy Name: Gann square 9   ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
import gradio as gr


# --- Gann Square of 9 Functions ---
def gann_square_of_9(price):
    if math.isnan(price):
        return []
    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)
    gann_values = [round((rounded + 0.125 * (i + 1)) ** 2, 2) for i in range(24)]
    return gann_values


def find_buy_sell_levels(price, gann_values):
    min_positive_index = next((i for i, v in enumerate(gann_values) if v >= price), -1)
    buy_above = gann_values[min_positive_index] if min_positive_index >= 0 else None
    sell_below = gann_values[min_positive_index - 1] if min_positive_index >= 0 else None
    return buy_above, sell_below


# --- ML Functions ---
def prepare_ml_data(df):
    df['atr'] = df['high'].rolling(5).max() - df['low'].rolling(5).min()
    df['dist_to_buy'] = df['buy_above'] - df['close']
    df['dist_to_sell'] = df['close'] - df['sell_below']
    df['target1_long'] = df['buy_above'] + (1 * df['atr'])
    df['target2_long'] = df['buy_above'] + (2 * df['atr'])
    df['target3_long'] = df['buy_above'] + (3 * df['atr'])
    df['target1_short'] = df['sell_below'] - (1 * df['atr'])
    df['target2_short'] = df['sell_below'] - (2 * df['atr'])
    df['target3_short'] = df['sell_below'] - (3 * df['atr'])
    return df.dropna()


def train_gann_target_model(df):
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    targets = ['target1_long', 'target2_long', 'target3_long',
               'target1_short', 'target2_short', 'target3_short']
    X, y = df[features], df[targets]
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    model = MultiOutputRegressor(RandomForestRegressor(n_estimators=100, random_state=42)).fit(X_train, y_train)
    print("Mean Absolute Error:", mean_absolute_error(y_test, model.predict(X_test)))
    return model


def predict_gann_targets(model, row):
    features = ['close', 'buy_above', 'sell_below', 'atr', 'dist_to_buy', 'dist_to_sell']
    return model.predict(row[features].to_numpy().reshape(1, -1))[0]


# --- Gann Strategy ---
def gann_strategy(price_data, timeframe, model):
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        gann_values = gann_square_of_9(current_price)
        buy_above, sell_below = find_buy_sell_levels(current_price, gann_values)
        row = price_data.iloc[i:i + 1]
        predicted_targets = predict_gann_targets(model, row)

        if buy_above and current_price >= buy_above:
            buy_targets = predicted_targets[:3]
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = predicted_targets[3:]
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))
    return signals


# --- Metrics Calculation ---
def calculate_metrics(signals, price_data):
    metrics = defaultdict(int)
    long_trades, short_trades = [], []
    long_pnl, short_pnl, all_pnls = [], [], []
    position = 0
    entry_price, entry_time, entry_quantity = 0, None, 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        if signal == 'buy' and position == 0:
            position, entry_price, entry_time, entry_quantity = 1, entry_level, timestamp, quantity
            long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets})
        elif signal == 'sell' and position == 0:
            position, entry_price, entry_time, entry_quantity = -1, entry_level, timestamp, quantity
            short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets})
        elif signal.startswith('exit') and position != 0:
            exit_price = price_data['close'].loc[timestamp]
            pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity
            all_pnls.append(pnl)
            if position == 1:
                long_trades[-1]['pnl'] = pnl
                long_pnl.append(pnl)
                metrics['long_trades'] += 1
                metrics['long_pnl'] += pnl
            else:
                short_trades[-1]['pnl'] = pnl
                short_pnl.append(pnl)
                metrics['short_trades'] += 1
                metrics['short_pnl'] += pnl
            position = 0

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    metrics['winning_trades'] = sum(1 for p in long_pnl + short_pnl if p > 0)
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'], metrics['sortino_ratio'] = 0, 0

    return metrics, long_trades, short_trades, all_pnls


# --- Visualization and Resampling ---
def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    fig, ax = plt.subplots(figsize=(12, 6))
    up, down = df[df.close >= df.open], df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, color="green")
    ax.bar(down.index, down.close - down.open, color="red")
    for signal, entry_level, targets, timestamp, _ in signals:
        color = 'g' if signal == 'buy' else 'r'
        ax.plot(timestamp, entry_level, 'o', color=color)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close()


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"PnL Curve ({timeframe})")
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    df = df.between_time('9:15', '15:30')
    resampled = df.resample(timeframe).agg({'open': 'first', 'high': 'max', 'low': 'min', 'close': 'last', 'volume': 'sum'})
    return resampled.dropna()


# --- Analyze Stock ---
def analyze_stock(stock_name, timeframe='5min'):
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)
    df = pd.read_parquet(os.path.join(stock_path, f"{stock_name}.parquet"))
    df['date'] = pd.to_datetime(df['datetime'])
    df.set_index('date', inplace=True)
    resampled_df = resample_data(df, timeframe)

    # Calculate Gann levels
    resampled_df['buy_above'], resampled_df['sell_below'] = zip(
        *resampled_df['close'].apply(lambda x: find_buy_sell_levels(x, gann_square_of_9(x)))
    )

    # Prepare ML data and train model
    prepared_df = prepare_ml_data(resampled_df)
    model = train_gann_target_model(prepared_df)

    # Generate signals
    signals = gann_strategy(prepared_df, timeframe, model)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Create charts and save
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save metrics and trades
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")

    metrics_df = pd.DataFrame([metrics])
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(long_trades)
    short_trades_df = pd.DataFrame(short_trades)
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Return results
    return metrics_df, trades_path, metrics_path, save_path


# --- Gradio Interface ---
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Textbox(label="Trades CSV Path"),
        gr.Textbox(label="Metrics CSV Path"),
        gr.Textbox(label="Save Path")
    ],
    title="Gann Strategy with ML-Enhanced Targets",
    description="Backtest Gann strategy with dynamically predicted multiple targets using ML integration."
)

iface.launch(debug=True)

ModuleNotFoundError: No module named 'gradio'

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.0 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'][i - 1]
        else:
            previous_price = price_data['close'][i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, price_data.index[i]))
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, price_data.index[i]))
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, price_data.index[i]))
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, price_data.index[i]))
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    all_pnls = []
    cumulative_pnl = 0

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        try:
            if signal == 'buy':
                long_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'sell':
                short_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'exit_buy':
                if long_trades:
                    trade = long_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['exit_price'] - trade['entry_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
            elif signal == 'exit_sell':
                if short_trades:
                    trade = short_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['entry_price'] - trade['exit_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for trade in long_trades if trade.get('pnl', 0) > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades']
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for trade in short_trades if trade.get('pnl', 0) > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades']
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://993e4204c18ca838c2.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


<ipython-input-4-4540e8a9fd9d>:362: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-4-4540e8a9fd9d>:362: FutureWarning: 'H' is deprecated and will be removed in a future version. Please use 'h' instead of 'H'.
  df_resampled = df.resample('1H', origin='epoch', offset='9H15min').agg({
<ipython-input-4-4540e8a9fd9d>:99: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
<ipython-input-4-4540e8a9fd9d>:107: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://993e4204c18ca838c2.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.1 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None for consistency
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    all_pnls = []
    cumulative_pnl = 0

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        try:
            if signal == 'buy':
                long_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'sell':
                short_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'exit_buy':
                if long_trades:
                    trade = long_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['exit_price'] - trade['entry_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
            elif signal == 'exit_sell':
                if short_trades:
                    trade = short_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['entry_price'] - trade['exit_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for trade in long_trades if trade.get('pnl', 0) > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades']
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for trade in short_trades if trade.get('pnl', 0) > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades']
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit
    cumulative_profit = 0
    for trade in long_trades + short_trades:
        cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
        trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://d56d7809b2ec0246ec.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
pip install gradio

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.2 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None for consistency
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    all_pnls = []
    cumulative_pnl = 0

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        try:
            if signal == 'buy':
                long_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'sell':
                short_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'exit_buy':
                if long_trades:
                    trade = long_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['exit_price'] - trade['entry_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
            elif signal == 'exit_sell':
                if short_trades:
                    trade = short_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['entry_price'] - trade['exit_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Long trades metrics
    metrics['long_winning_trades'] = sum(1 for trade in long_trades if trade.get('pnl', 0) > 0)
    metrics['long_losing_trades'] = metrics['long_trades'] - metrics['long_winning_trades']
    metrics['long_win_rate'] = metrics['long_winning_trades'] / metrics['long_trades'] if metrics['long_trades'] > 0 else 0

    # Short trades metrics
    metrics['short_winning_trades'] = sum(1 for trade in short_trades if trade.get('pnl', 0) > 0)
    metrics['short_losing_trades'] = metrics['short_trades'] - metrics['short_winning_trades']
    metrics['short_win_rate'] = metrics['short_winning_trades'] / metrics['short_trades'] if metrics['short_trades'] > 0 else 0

    # Overall winning metrics
    metrics['winning_trades'] = metrics['long_winning_trades'] + metrics['short_winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
    else:
        metrics['avg_long_pnl'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
    else:
        metrics['avg_short_pnl'] = 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.2 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None for consistency
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    all_pnls = []
    cumulative_pnl = 0

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        try:
            if signal == 'buy':
                long_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'sell':
                short_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'exit_buy':
                if long_trades:
                    trade = long_trades.pop()  # Remove the last long trade
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['exit_price'] - trade['entry_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
            elif signal == 'exit_sell':
                if short_trades:
                    trade = short_trades.pop()  # Remove the last short trade
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['entry_price'] - trade['exit_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Long trades metrics
    metrics['long_winning_trades'] = sum(1 for trade in long_trades if trade.get('pnl', 0) > 0)
    metrics['long_losing_trades'] = metrics['long_trades'] - metrics['long_winning_trades']
    metrics['long_win_rate'] = metrics['long_winning_trades'] / metrics['long_trades'] if metrics['long_trades'] > 0 else 0

    # Short trades metrics
    metrics['short_winning_trades'] = sum(1 for trade in short_trades if trade.get('pnl', 0) > 0)
    metrics['short_losing_trades'] = metrics['short_trades'] - metrics['short_winning_trades']
    metrics['short_win_rate'] = metrics['short_winning_trades'] / metrics['short_trades'] if metrics['short_trades'] > 0 else 0

    # Overall winning metrics
    metrics['winning_trades'] = metrics['long_winning_trades'] + metrics['short_winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
    else:
        metrics['avg_long_pnl'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
    else:
        metrics['avg_short_pnl'] = 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls



def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
                      'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}
    all_trades = {timeframe: {'long_trades': long_trades, 'short_trades': short_trades}}

    # Calculate cumulative profit (this seems redundant since it's already in calculate_metrics)
    # cumulative_profit = 0
    # for trade in long_trades + short_trades:
    #     cumulative_profit += trade.get('pnl', 0)  # Handle potential KeyError
    #     trade['cumulative_profit'] = cumulative_profit

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)

    long_trades_df = pd.DataFrame(all_trades[timeframe]['long_trades'])
    short_trades_df = pd.DataFrame(all_trades[timeframe]['short_trades'])
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)
    all_trades_df.to_csv(trades_path, index=False)

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://8b860cbf76df5d904f.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.3 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None for consistency
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    all_pnls = []
    cumulative_pnl = 0

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        try:
            if signal == 'buy':
                long_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'sell':
                short_trades.append({
                    'entry_time': timestamp, 'entry_price': entry_price,
                    'stop_loss_price': stop_loss_price, 'quantity': quantity
                })
            elif signal == 'exit_buy':
                if long_trades:
                    trade = long_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['exit_price'] - trade['entry_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
            elif signal == 'exit_sell':
                if short_trades:
                    trade = short_trades.pop()
                    trade['exit_time'] = timestamp
                    trade['exit_price'] = entry_price
                    pnl = (trade['entry_price'] - trade['exit_price']) * trade['quantity']
                    trade['pnl'] = pnl
                    cumulative_pnl += pnl
                    trade['cumulative_pnl'] = cumulative_pnl
                    all_pnls.append(pnl)
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # --- Calculate Metrics ---

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']  # Corrected calculation
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    # Long trades metrics
    long_winning_trades = sum(1 for trade in long_trades if trade.get('pnl', 0) > 0)  # Calculate here
    long_losing_trades = len(long_trades) - long_winning_trades  # Calculate here
    metrics['long_winning_trades'] = long_winning_trades
    metrics['long_losing_trades'] = long_losing_trades
    metrics['long_win_rate'] = long_winning_trades / len(long_trades) if len(long_trades) > 0 else 0
    metrics['avg_long_pnl'] = metrics['long_pnl'] / len(long_trades) if len(long_trades) > 0 else 0

    # Short trades metrics
    short_winning_trades = sum(1 for trade in short_trades if trade.get('pnl', 0) > 0)  # Calculate here
    short_losing_trades = len(short_trades) - short_winning_trades  # Calculate here
    metrics['short_winning_trades'] = short_winning_trades
    metrics['short_losing_trades'] = short_losing_trades
    metrics['short_win_rate'] = short_winning_trades / len(short_trades) if len(short_trades) > 0 else 0
    metrics['avg_short_pnl'] = metrics['short_pnl'] / len(short_trades) if len(short_trades) > 0 else 0

    # Overall winning metrics
    metrics['winning_trades'] = long_winning_trades + short_winning_trades
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # Create trades DataFrame (corrected)
    long_trades_df = pd.DataFrame(long_trades)
    short_trades_df = pd.DataFrame(short_trades)
    long_trades_df['trade_type'] = 'long'
    short_trades_df['trade_type'] = 'short'
    all_trades_df = pd.concat([long_trades_df, short_trades_df], ignore_index=True)

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, trades_df, chart_path, pnl_path  # Return the correct trades DataFrame


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://7de2a2a85ec3d44729.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.4 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None for consistency
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Add None
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://72b5dcc0b18f2f03c0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Err

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://72b5dcc0b18f2f03c0.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.5 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0  # Initialize entry_quantity

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
            entry_quantity = quantity  # Store the quantity
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1
            entry_quantity = quantity  # Store the quantity

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel   ("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://2cc0a7e53d73edde57.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Err

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://2cc0a7e53d73edde57.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.6 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0  # Initialize entry_quantity

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
            entry_quantity = quantity  # Store the quantity
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1
            entry_quantity = quantity  # Store the quantity

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    # ... (the beginning of the function remains the same)

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Calculate long_wins here
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)  # Calculate short_wins here
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins  # Now you can use long_wins and short_wins
    # ... (the rest of the function remains the same)

    #metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://f6090650e632406eb8.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Error free code from gemini

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.7 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    if math.isnan(price):
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
    else:
        buy_above = None
        sell_below = None

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
    except ValueError:
        pass  # Handle cases where entry_level is not found
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0  # Initialize entry_quantity

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use .iloc

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = 1
            entry_quantity = quantity  # Store the quantity
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Example stop-loss
            quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, quantity, price_data.index[i]))
            position = -1
            entry_quantity = quantity  # Store the quantity

        # Exit conditions (with stop-loss)
        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                position = 0
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, None, None, price_data.index[i]))  # Consistent signal format
                        position = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
            elif signal.startswith('exit') and position != 0:
                exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time
                pnl = (exit_price - entry_price) * entry_quantity if position == 1 else (entry_price - exit_price) * entry_quantity  # Calculate PnL with quantity
                all_pnls.append(pnl)  # Add PnL to the list

                if position == 1:
                    long_trades[-1]['exit_time'] = timestamp
                    long_trades[-1]['exit_price'] = exit_price
                    long_trades[-1]['pnl'] = pnl
                    metrics['long_trades'] += 1
                    metrics['long_pnl'] += pnl
                    long_pnl.append(pnl)
                else:
                    short_trades[-1]['exit_time'] = timestamp
                    short_trades[-1]['exit_price'] = exit_price
                    short_trades[-1]['pnl'] = pnl
                    metrics['short_trades'] += 1
                    metrics['short_pnl'] += pnl
                    short_pnl.append(pnl)

                position = 0
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Calculate long_wins here
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)  # Calculate short_wins here
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins  # Now you can use long_wins and short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:       df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://9e340c1fd003e0564d.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_buy, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_sell, Error: None
Error processing signal: exit_buy, Error: None
Err

In [ ]:
!pip install gradio

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.8 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.

    Returns:
        A list of Gann Square of 9 values, or an empty list if price is NaN.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}")  # Debug statement
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")  # Debug statement
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(24):
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))  # Round to 2 decimal places

    print(f"DEBUG: Calculated Gann values: {gann_values}")  # Debug statement
    return gann_values


def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")  # Debug statement
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")  # Debug statement
    else:
        buy_above = None
        sell_below = None
        print("DEBUG: No buy/sell levels found.")  # Debug statement

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}")  # Debug statement
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
        print(f"DEBUG: Calculated targets: {targets}")  # Debug statement
    except ValueError:
        print("DEBUG: Entry level not found in Gann values.")  # Debug statement
        pass  # Handle cases where entry_level is not found
    return targets

#def gann_strategy(price_data, timeframe):
def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")  # Debug statement
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]  # Use .iloc for position-based indexing
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'].iloc[i - 1]  # Use the previous day's closing price
        else:
            previous_price = price_data['close'].iloc[i - 1]  # Use the previous candle's closing price

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            # Include quantity in the signal
            quantity = calculate_quantity(capital, buy_above, risk_percentage, buy_above * 0.98)  # Example stop-loss
            signals.append(('buy', buy_above, buy_targets, price_data.index[i], quantity))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            # Include quantity in the signal
            quantity = calculate_quantity(capital, sell_below, risk_percentage, sell_below * 1.02)  # Example stop-loss
            signals.append(('sell', sell_below, sell_targets, price_data.index[i], quantity))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i], None))  # Include None for quantity
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i], None))  # Include None for quantity

    return signals


# ... (rest of the code remains the same)




def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")  # Debug statement
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")  # Debug statement
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")  # Debug statement
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")  # Debug statement
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing BUY signal at {timestamp}")  # Debug statement
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing SELL signal at {timestamp}")  # Debug statement
            elif signal.startswith('exit') and position != 0:
                # --- Check if there's an open trade before processing exit ---
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time

                    # --- Corrected PnL calculation ---
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity
                    # --- End of correction ---

                    all_pnls.append(pnl)  # Add PnL to the list

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")  # Debug statement
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")  # Debug statement

                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
                # --- End of check ---
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Calculate long_wins here
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)  # Calculate short_wins here
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins  # Now you can use long_wins and short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    print("DEBUG: Trading metrics calculated successfully.")  # Debug statement
    return metrics, long_trades, short_trades, all_pnls



def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")  # Debug statement
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory
    print("DEBUG: Candlestick chart plotted and saved successfully.")  # Debug statement


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")  # Debug statement
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")  # Debug statement


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")  # Debug statement
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")  # Debug statement
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")  # Debug statement
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")  # Debug statement
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://fa3195b77a375ef625.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Streaming output truncated to the last 5000 lines.
DEBUG: Calculated targets: [1156.0, 1164.52, 1173.06, 1181.64]
DEBUG: Calculating quantity for capital: 100000, entry price: 1147.52, risk percentage: 1, stop-loss price: 1124.5696
DEBUG: Calculated quantity: 43
DEBUG: Calculating Gann Square of 9 values for price: 1156.5
DEBUG: Calculated Gann values: [1097.27, 1105.56, 1113.89, 1122.25, 1130.64, 1139.06, 1147.52, 1156.0, 1164.52, 1173.06, 1181.64, 1190.25, 1198.89, 1207.56, 1216.27, 1225.0, 1233.77, 1242.56, 1251.39, 1260.25, 1269.14, 1278.06, 1287.02, 1296.0]
DEBUG: Finding buy/sell levels for price: 1156.5, Gann values: [1097.27, 1105.56, 1113.89, 1122.25, 1130.64, 1139.06, 1147.52, 1156.0, 1164.52, 1173.06, 1181.64, 1190.25, 1198.89, 1207.56, 1216.27, 1225.0, 1233.77, 1242.56, 1251.39, 1260.25, 1269.14, 1278.06, 1287.02, 1296.0]
DEBUG: Buy above: 1164.52, Sell below: 1156.0
DEBUG: Calculating targets for entry level: 1156.0, direction: short
DEBUG: Calculated targets: [1147.52, 11

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 2.9 (Improved)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
from scipy.stats import skew, kurtosis
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):  # Calculate only required levels
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values by returning an empty list.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate (default 5).

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}")  # Debug statement
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")  # Debug statement
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = []
    for i in range(num_levels * 8):  # Calculate enough values for long/short targets
        x = rounded + 0.125 * (i + 1)
        gann_values.append(round(x * x, 2))

    print(f"DEBUG: Calculated Gann values: {gann_values}")  # Debug statement
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")  # Debug statement
    min_positive_index = next((i for i, value in enumerate(gann_values) if value > price), None)

    if min_positive_index is not None:
        buy_above = gann_values[min_positive_index]
        sell_below = gann_values[min_positive_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")  # Debug statement
    else:
        buy_above = None
        sell_below = None
        print("DEBUG: No buy/sell levels found.")  # Debug statement

    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}")  # Debug statement
    targets = []
    try:
        start_index = gann_values.index(entry_level)
        if direction == 'long':
            targets = gann_values[start_index + 1: start_index + 5]
        elif direction == 'short':
            targets = gann_values[start_index - 1: start_index - 5: -1]
        print(f"DEBUG: Calculated targets: {targets}")  # Debug statement
    except ValueError:
        print("DEBUG: Entry level not found in Gann values.")  # Debug statement
        pass  # Handle cases where entry_level is not found
    return targets

#def gann_strategy(price_data, timeframe):
#   """
def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions,
    using previous day's close for the first candle of the day.
    """
    signals = []
    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'][i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        if current_date != previous_date:
            previous_price = price_data['close'][i - 1]  # Use the previous day's closing price
        else:
            previous_price = price_data['close'][i - 1]  # Use the previous candle's closing price

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above:
            buy_targets = calculate_targets(buy_above, gann_values, direction='long')
            signals.append(('buy', buy_above, buy_targets, price_data.index[i]))
        elif sell_below and current_price <= sell_below:
            sell_targets = calculate_targets(sell_below, gann_values, direction='short')
            signals.append(('sell', sell_below, sell_targets, price_data.index[i]))

        # Basic exit conditions (you can customize these)
        if signals and signals[-1][0] == 'buy':
            for j, target in enumerate(signals[-1][2]):
                if current_price >= target:
                    signals.append(('exit_buy', target, j+1, price_data.index[i]))
        elif signals and signals[-1][0] == 'sell':
            for j, target in enumerate(signals[-1][2]):
                if current_price <= target:
                    signals.append(('exit_sell', target, j+1, price_data.index[i]))

    return signals



def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")  # Debug statement
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")  # Debug statement
        return 0  # Avoid division by zero
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")  # Debug statement
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")  # Debug statement
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []  # List to store all PnLs

    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    entry_time = None
    entry_quantity = 0  # Store the entry quantity

    for signal, entry_level, targets, timestamp, quantity in signals:  # Include quantity
        try:  # Add a try-except block to handle potential errors
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing BUY signal at {timestamp}")  # Debug statement
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity  # Store the quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing SELL signal at {timestamp}")  # Debug statement
            elif signal.startswith('exit') and position != 0:
                # --- Check if there's an open trade before processing exit ---
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]  # Get close price at exit time

                    # --- Corrected PnL calculation ---
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity
                    # --- End of correction ---

                    all_pnls.append(pnl)  # Add PnL to the list

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")  # Debug statement
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")  # Debug statement

                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
                # --- End of check ---
        except Exception as e:
            print(f"Error processing signal: {signal}, Error: {e}")

    # Calculate other metrics
    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Calculate long_wins here
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)  # Calculate short_wins here
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins  # Now you can use long_wins and short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    print("DEBUG: Trading metrics calculated successfully.")  # Debug statement
    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")  # Debug statement
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open,color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)  # Close the figure to free up memory
    print("DEBUG: Candlestick chart plotted and saved successfully.")  # Debug statement


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.

    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")  # Debug statement
    cumulative_pnls = np.cumsum(pnls)  # Calculate cumulative PnLs for this timeframe
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    # Save the PnL curve
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")  # Debug statement


def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")  # Debug statement
    # Ensure the DataFrame index is localized to Indian Standard Time
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    # Filter data to NSE trading hours (9:15 to 15:30)
    df = df.between_time('9:15', '15:30')

    # Resample with custom anchor (9:15)
    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({  # Use 'h'
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:  # For '5min', '15min', or other intervals, standard resampling
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    # Drop any intervals that fall outside the market hours
    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")  # Debug statement
    return df_resampled


def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")  # Debug statement
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    # Construct file paths
    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    # Read and preprocess data
    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None  # Or handle the error as needed

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    # Resample data
    resampled_df = resample_data(df.copy(), timeframe)  # Create a copy of df

    # Apply Gann strategy
    signals = gann_strategy(resampled_df, timeframe)

    # Calculate metrics
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)

    # Store metrics and trades
    all_metrics = {timeframe: metrics}

    # --- Create trades DataFrame (corrected) ---
    trades_list = []
    for trade in long_trades:  # Add long trades to the list
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:  # Add short trades to the list
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)  # Create DataFrame from the list

    # Plot charts
    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    # Save results
    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)  # Save the trades DataFrame

    # Load and return results
    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")  # Debug statement
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

# Set your initial capital and risk percentage
capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# Create the Gradio interface
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://eddca7a4a2c6b55160.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


DEBUG: Analyzing stock: AMARAJ, timeframe: 1H
DEBUG: Resampling data for timeframe: 1H
DEBUG: Data resampled successfully.
DEBUG: Calculating Gann Square of 9 values for price: 620.6
DEBUG: Calculated Gann values: [534.77, 540.56, 546.39, 552.25, 558.14, 564.06, 570.02, 576.0, 582.02, 588.06, 594.14, 600.25, 606.39, 612.56, 618.77, 625.0, 631.27, 637.56, 643.89, 650.25, 656.64, 663.06, 669.52, 676.0, 682.52, 689.06, 695.64, 702.25, 708.89, 715.56, 722.27, 729.0, 735.77, 742.56, 749.39, 756.25, 763.14, 770.06, 777.02, 784.0]
DEBUG: Finding buy/sell levels for price: 620.6, Gann values: [534.77, 540.56, 546.39, 552.25, 558.14, 564.06, 570.02, 576.0, 582.02, 588.06, 594.14, 600.25, 606.39, 612.56, 618.77, 625.0, 631.27, 637.56, 643.89, 650.25, 656.64, 663.06, 669.52, 676.0, 682.52, 689.06, 695.64, 702.25, 708.89, 715.56, 722.27, 729.0, 735.77, 742.56, 749.39, 756.25, 763.14, 770.06, 777.02, 784.0]
DEBUG: Buy above: 625.0, Sell below: 618.77
DEBUG: Calculating Gann Square of 9 values for p

<ipython-input-20-30419373b509>:107: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_price = price_data['close'][i]
<ipython-input-20-30419373b509>:115: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = price_data['close'][i - 1]  # Use the previous candle's closing price
<ipython-input-20-30419373b509>:113: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  previous_price = price_data['close'][i - 1]  # Use the previo

Streaming output truncated to the last 5000 lines.
DEBUG: Buy above: 798.06, Sell below: 791.02
DEBUG: Calculating Gann Square of 9 values for price: 793.85
DEBUG: Calculated Gann values: [735.77, 742.56, 749.39, 756.25, 763.14, 770.06, 777.02, 784.0, 791.02, 798.06, 805.14, 812.25, 819.39, 826.56, 833.77, 841.0, 848.27, 855.56, 862.89, 870.25, 877.64, 885.06, 892.52, 900.0, 907.52, 915.06, 922.64, 930.25, 937.89, 945.56, 953.27, 961.0, 968.77, 976.56, 984.39, 992.25, 1000.14, 1008.06, 1016.02, 1024.0]
DEBUG: Finding buy/sell levels for price: 793.85, Gann values: [735.77, 742.56, 749.39, 756.25, 763.14, 770.06, 777.02, 784.0, 791.02, 798.06, 805.14, 812.25, 819.39, 826.56, 833.77, 841.0, 848.27, 855.56, 862.89, 870.25, 877.64, 885.06, 892.52, 900.0, 907.52, 915.06, 922.64, 930.25, 937.89, 945.56, 953.27, 961.0, 968.77, 976.56, 984.39, 992.25, 1000.14, 1008.06, 1016.02, 1024.0]
DEBUG: Buy above: 798.06, Sell below: 791.02
DEBUG: Calculating targets for entry level: 791.02, direction: s

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/gradio/queueing.py", line 624, in process_events
    response = await route_utils.call_process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 2015, in process_api
    result = await self.call_function(
  File "/usr/local/lib/python3.10/dist-packages/gradio/blocks.py", line 1562, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
  File "/usr/local/lib/python3.10/dist-packages/anyio/to_thread.py", line 33, in run_sync
    return await get_asynclib().run_sync_in_worker_thread(
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 877, in run_sync_in_worker_thread
    return await future
  File "/usr/local/lib/python3.10/dist-packages/anyio/_backends/_asyncio.py", line 8

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://eddca7a4a2c6b55160.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (Refined)        ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import dateutil.rrule
import gradio as gr

def gann_square_of_9(price, num_levels=5):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + 0.125 * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    if direction == 'long':
        targets = gann_values[start_index + 1 : start_index + 5]
    elif direction == 'short':
        targets = gann_values[start_index - 1 : start_index - 5 : -1]
    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        previous_price = price_data['close'].iloc[i - 1] if current_date != previous_date else price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i]))
            position = 1
            print(f"DEBUG: Generated BUY signal at {price_data.index[i]}")
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i]))
            position = -1
            print(f"DEBUG: Generated SELL signal at {price_data.index[i]}")

        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT BUY signal (stop-loss) at {price_data.index[i]}")
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT BUY signal (target) at {price_data.index[i]}")
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT SELL signal (stop-loss) at {price_data.index[i]}")
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT SELL signal (target) at {price_data.index[i]}")
                        break

    print("DEBUG: Gann strategy applied successfully.")
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, targets, timestamp, quantity in signals:
        try:
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'targets': targets, 'quantity': quantity})
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity
                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0  # Initialize long_wins here
    short_wins = 0  # Initialize short_wins here

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)  # Calculate long_wins here
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)  # Calculate short_wins here
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins  # Now you can use long_wins and short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    # Calculate Sharpe and Sortino ratios (assuming a risk-free rate of 0)
    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    print("DEBUG: Trading metrics calculated successfully.")
    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    signals = gann_strategy(resampled_df, timeframe)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path

# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://e02914d342397e193f.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Streaming output truncated to the last 5000 lines.
DEBUG: Calculating Gann Square of 9 values for price: 1145.9
DEBUG: Calculated Gann values: [1032.02, 1040.06, 1048.14, 1056.25, 1064.39, 1072.56, 1080.77, 1089.0, 1097.27, 1105.56, 1113.89, 1122.25, 1130.64, 1139.06, 1147.52, 1156.0, 1164.52, 1173.06, 1181.64, 1190.25, 1198.89, 1207.56, 1216.27, 1225.0, 1233.77, 1242.56, 1251.39, 1260.25, 1269.14, 1278.06, 1287.02, 1296.0, 1305.02, 1314.06, 1323.14, 1332.25, 1341.39, 1350.56, 1359.77, 1369.0]
DEBUG: Finding buy/sell levels for price: 1145.9, Gann values: [1032.02, 1040.06, 1048.14, 1056.25, 1064.39, 1072.56, 1080.77, 1089.0, 1097.27, 1105.56, 1113.89, 1122.25, 1130.64, 1139.06, 1147.52, 1156.0, 1164.52, 1173.06, 1181.64, 1190.25, 1198.89, 1207.56, 1216.27, 1225.0, 1233.77, 1242.56, 1251.39, 1260.25, 1269.14, 1278.06, 1287.02, 1296.0, 1305.02, 1314.06, 1323.14, 1332.25, 1341.39, 1350.56, 1359.77, 1369.0]
DEBUG: Buy above: 1147.52, Sell below: 1139.06
DEBUG: Calculating targets for entr

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.0 (Refined)        ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr  # Import gradio

def gann_square_of_9(price, num_levels=5):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + 0.125 * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    if direction == 'long':
        targets = gann_values[start_index + 1 : start_index + 5]
    elif direction == 'short':
        targets = gann_values[start_index - 1 : start_index - 5 : -1]
    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        previous_price = price_data['close'].iloc[i - 1] if current_date != previous_date else price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i]))
            position = 1
            print(f"DEBUG: Generated BUY signal at {price_data.index[i]}")
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i]))
            position = -1
            print(f"DEBUG: Generated SELL signal at {price_data.index[i]}")

        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT BUY signal (stop-loss) at {price_data.index[i]}")
            else:
                targets = calculate_targets(entry_price, gann_values, direction='long')
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT BUY signal (target) at {price_data.index[i]}")
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT SELL signal (stop-loss) at {price_data.index[i]}")
            else:
                targets = calculate_targets(entry_price, gann_values, direction='short')
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i]))
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT SELL signal (target) at {price_data.index[i]}")
                        break

    print("DEBUG: Gann strategy applied successfully.")
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp in signals:
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity})
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity})
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity
                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    print("DEBUG: Trading metrics calculated successfully.")
    return metrics, long_trades, short_trades, all_pnls


def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    for signal, entry_price, stop_loss_price, quantity, timestamp in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe       timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    signals = gann_strategy(resampled_df, timeframe)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path

# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# --- Gradio Interface ---
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://13d691dbf04f78b14c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Streaming output truncated to the last 5000 lines.
DEBUG: Calculating targets for entry level: 1444.0, direction: short
DEBUG: Calculated targets: [1434.52, 1425.06, 1415.64, 1406.25]
DEBUG: Calculating Gann Square of 9 values for price: 1441.4
DEBUG: Calculated Gann values: [1305.02, 1314.06, 1323.14, 1332.25, 1341.39, 1350.56, 1359.77, 1369.0, 1378.27, 1387.56, 1396.89, 1406.25, 1415.64, 1425.06, 1434.52, 1444.0, 1453.52, 1463.06, 1472.64, 1482.25, 1491.89, 1501.56, 1511.27, 1521.0, 1530.77, 1540.56, 1550.39, 1560.25, 1570.14, 1580.06, 1590.02, 1600.0, 1610.02, 1620.06, 1630.14, 1640.25, 1650.39, 1660.56, 1670.77, 1681.0]
DEBUG: Finding buy/sell levels for price: 1441.4, Gann values: [1305.02, 1314.06, 1323.14, 1332.25, 1341.39, 1350.56, 1359.77, 1369.0, 1378.27, 1387.56, 1396.89, 1406.25, 1415.64, 1425.06, 1434.52, 1444.0, 1453.52, 1463.06, 1472.64, 1482.25, 1491.89, 1501.56, 1511.27, 1521.0, 1530.77, 1540.56, 1550.39, 1560.25, 1570.14, 1580.06, 1590.02, 1600.0, 1610.02, 1620.06, 16

This 3.2 version improved with targets tracking and updating targets in the tradelogs

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.2 (Target Tracking) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr

def gann_square_of_9(price, num_levels=5):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + 0.125 * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long'):
    """
    Calculates target levels based on trade direction.

    Args:
        entry_level: The entry level (buy_above or sell_below).
        gann_values: A list of Gann Square of 9 values.
        direction: 'long' or 'short' indicating the trade direction.

    Returns:
        A list of target levels.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    if direction == 'long':
        targets = gann_values[start_index + 1 : start_index + 5]
    elif direction == 'short':
        targets = gann_values[start_index - 1 : start_index - 5 : -1]
    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        previous_price = price_data['close'].iloc[i - 1] if current_date != previous_date else price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='long')  # Calculate targets
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))  # Include targets in the signal
            position = 1
            print(f"DEBUG: Generated BUY signal at {price_data.index[i]}")
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='short')  # Calculate targets
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))  # Include targets in the signal
            position = -1
            print(f"DEBUG: Generated SELL signal at {price_data.index[i]}")

        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))  # Empty targets for stop-loss exit
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT BUY signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))  # Empty targets for target exit
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT BUY signal (target) at {price_data.index[i]}")
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))  # Empty targets for stop-loss exit
                position = 0
                entry_quantity = 0  # Reset quantity after exit
                print(f"DEBUG: Generated EXIT SELL signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))  # Empty targets for target exit
                        position = 0
                        entry_quantity = 0  # Reset quantity after exit
                        print(f"DEBUG: Generated EXIT SELL signal (target) at {price_data.index[i]}")
                        break

    print("DEBUG: Gann strategy applied successfully.")
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp, targets in signals:
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}, Targets: {targets}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity

                        # Check which long targets were hit
                        for i, target in enumerate(long_trades[-1]['targets']):
                            if exit_price >= target:
                                long_trades[-1]['targets_hit'].append(i + 1)
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity

                        # Check which short targets were hit
                        for i, target in enumerate(short_trades[-1]['targets']):
                            if exit_price <= target:
                                short_trades[-1]['targets_hit'].append(i + 1)

                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    # --- Target Hit Metrics ---
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    # Add target hit counts to metrics
    for target_num, hits in target_hits.items():
        metrics[f'target_{target_num}_hits_long'] = hits['long']
        metrics[f'target_{target_num}_hits_short'] = hits['short']

    # --- End of Target Hit Metrics ---

    print("DEBUG: Trading metrics calculated successfully.")

    # Analyze target hit data (optional)
    analyze_target_hits(long_trades, short_trades)

    return metrics, long_trades, short_trades, all_pnls


def analyze_target_hits(long_trades, short_trades):
    """
    Analyzes the frequency of target hits.
    """
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    print("Target Hit Frequency:")
    for target_num, hits in target_hits.items():
        print(f"  Target {target_num}: Long - {hits['long']}, Short - {hits['short']}")

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp, targets in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    signals = gann_strategy(resampled_df, timeframe)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path

# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# --- Gradio Interface ---
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://2b3edfcac917f7bfef.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Streaming output truncated to the last 5000 lines.
DEBUG: Buy above: 12740.77, Sell below: 12712.56
DEBUG: Calculating Gann Square of 9 values for price: 12781.5
DEBUG: Calculated Gann values: [12572.02, 12600.06, 12628.14, 12656.25, 12684.39, 12712.56, 12740.77, 12769.0, 12797.27, 12825.56, 12853.89, 12882.25, 12910.64, 12939.06, 12967.52, 12996.0, 13024.52, 13053.06, 13081.64, 13110.25, 13138.89, 13167.56, 13196.27, 13225.0, 13253.77, 13282.56, 13311.39, 13340.25, 13369.14, 13398.06, 13427.02, 13456.0, 13485.02, 13514.06, 13543.14, 13572.25, 13601.39, 13630.56, 13659.77, 13689.0]
DEBUG: Finding buy/sell levels for price: 12781.5, Gann values: [12572.02, 12600.06, 12628.14, 12656.25, 12684.39, 12712.56, 12740.77, 12769.0, 12797.27, 12825.56, 12853.89, 12882.25, 12910.64, 12939.06, 12967.52, 12996.0, 13024.52, 13053.06, 13081.64, 13110.25, 13138.89, 13167.56, 13196.27, 13225.0, 13253.77, 13282.56, 13311.39, 13340.25, 13369.14, 13398.06, 13427.02, 13456.0, 13485.02, 13514.06, 13543.14, 

Creating this experiment using volatility based gann angles for targets

In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.3 (Volatility-Based) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr

def gann_square_of_9(price, num_levels=5, increment=0.125):  # Add increment parameter
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.
        increment: The increment to use for calculating Gann levels.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}, increment: {increment}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + increment * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long', angles=[0.125, 0.25, 0.5, 0.75, 1.0]):
    """
    Calculates target levels based on trade direction and given angles.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}, angles: {angles}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    targets = []
    if direction == 'long':
        for angle in angles:
            target_index = start_index + int(angle * 8)  # Calculate target index based on angle
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])
    elif direction == 'short':
        for angle in angles:
            target_index = start_index - int(angle * 8)
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])

    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe):
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    # --- Volatility-Based Angles ---
    volatility = calculate_volatility(price_data)
    volatility_range = get_volatility_range(volatility)
    target_angles = angle_config.get(volatility_range, angle_config['low'])
    # --- End of Volatility-Based Angles ---

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        previous_price = price_data['close'].iloc[i - 1] if current_date != previous_date else price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)  # Use default increment (0.125) for entry signals
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Adjust SL based on volatility (example)
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='long', angles=target_angles)
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))
            position = 1
            print(f"DEBUG: Generated BUY signal at {price_data.index[i]}")
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Adjust SL based on volatility (example)
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='short', angles=target_angles)
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))
            position = -1
            print(f"DEBUG: Generated SELL signal at {price_data.index[i]}")

        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                position = 0
                entry_quantity = 0
                print(f"DEBUG: Generated EXIT BUY signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                        position = 0
                        entry_quantity = 0
                        print(f"DEBUG: Generated EXIT BUY signal (target) at {price_data.index[i]}")
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                position = 0
                entry_quantity = 0
                print(f"DEBUG: Generated EXIT SELL signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                        position = 0
                        entry_quantity = 0
                        print(f"DEBUG: Generated EXIT SELL signal (target) at {price_data.index[i]}")
                        break

    print("DEBUG: Gann strategy applied successfully.")
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")  # Corrected indentation
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp, targets in signals:
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}, Targets: {targets}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity

                        # Check which long targets were hit
                        for i, target in enumerate(long_trades[-1]['targets']):
                            if exit_price >= target:
                                long_trades[-1]['targets_hit'].append(i + 1)
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity

                        # Check which short targets were hit
                        for i, target in enumerate(short_trades[-1]['targets']):
                            if exit_price <= target:
                                short_trades[-1]['targets_hit'].append(i + 1)

                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    # --- Target Hit Metrics ---
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    # Add target hit counts to metrics
    for target_num, hits in target_hits.items():
        metrics[f'target_{target_num}_hits_long'] = hits['long']
        metrics[f'target_{target_num}_hits_short'] = hits['short']

    # --- End of Target Hit Metrics ---

    print("DEBUG: Trading metrics calculated successfully.")

    # Analyze target hit data (optional)
    analyze_target_hits(long_trades, short_trades)

    return metrics, long_trades, short_trades, all_pnls

def analyze_target_hits(long_trades, short_trades):
    """
    Analyzes the frequency of target hits.
    """
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    print("Target Hit Frequency:")
    for target_num, hits in target_hits.items():
        print(f"Target {target_num}: Long - {hits['long']}, Short - {hits['short']}")

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp, targets in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def calculate_volatility(df, period=20):  # Calculate volatility over 20 periods (e.g., days)
    """
    Calculates the volatility of a stock.
    """
    df['pct_change'] = df['close'].pct_change()
    volatility = df['pct_change'].rolling(window=period).std() * 100  # Convert to percentage
    return volatility.iloc[-1]  # Return the latest volatility value

def get_volatility_range(volatility):
    """
    Determines the volatility range based on volatility value.
    """
    if volatility < 2:
        return 'low'
    elif volatility < 5:
        return 'medium'
    else:
        return 'high'

# --- Volatility-Based Angle Configuration ---
angle_config = {
    'low': [0.125, 0.25, 0.5, 0.75, 1.0],
    'medium': [0.25, 0.5, 1.0, 1.5, 2.0],
    'high': [0.5, 1.0, 2.0, 3.0, 4.0]
}
# --- End of Volatility-Based Angle Configuration ---

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
               print(f"Error: Data file not found for {stock_name} at {file_path}")
    return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    signals = gann_strategy(resampled_df, timeframe)
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path

# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# --- Gradio Interface ---
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://81cc6a43991930516c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


DEBUG: Analyzing stock: MARUTI, timeframe: 1H
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://81cc6a43991930516c.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.3 (Volatility-Based) ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr

def gann_square_of_9(price, num_levels=5, increment=0.125):  # Add increment parameter
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.
        increment: The increment to use for calculating Gann levels.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}, increment: {increment}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + increment * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long', angles=[0.125, 0.25, 0.5, 0.75, 1.0]):
    """
    Calculates target levels based on trade direction and given angles.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}, angles: {angles}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    targets = []
    if direction == 'long':
        for angle in angles:
            target_index = start_index + int(angle * 8)  # Calculate target index based on angle
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])
    elif direction == 'short':
        for angle in angles:
            target_index = start_index - int(angle * 8)
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])

    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe, target_angles):  # Add target_angles as a parameter
    """
    Implements the Gann strategy with target levels and exit conditions.
    """
    # ... (rest of the function remains the same) ...

    print(f"DEBUG: Applying Gann strategy for timeframe: {timeframe}")
    signals = []
    position = 0  # 1 for long, -1 for short, 0 for no position
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    # --- Volatility-Based Angles ---
    volatility = calculate_volatility(price_data)
    volatility_range = get_volatility_range(volatility)
    target_angles = angle_config.get(volatility_range, angle_config['low'])
    # --- End of Volatility-Based Angles ---

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        current_date = price_data.index[i].date()
        previous_date = price_data.index[i - 1].date()

        # Use previous day's close for the first candle of the day
        previous_price = price_data['close'].iloc[i - 1] if current_date != previous_date else price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)  # Use default increment (0.125) for entry signals
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = entry_price * 0.98  # Adjust SL based on volatility (example)
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='long', angles=target_angles)
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))
            position = 1
            print(f"DEBUG: Generated BUY signal at {price_data.index[i]}")
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = entry_price * 1.02  # Adjust SL based on volatility (example)
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='short', angles=target_angles)
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets))
            position = -1
            print(f"DEBUG: Generated SELL signal at {price_data.index[i]}")

        if position == 1:
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                position = 0
                entry_quantity = 0
                print(f"DEBUG: Generated EXIT BUY signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                        position = 0
                        entry_quantity = 0
                        print(f"DEBUG: Generated EXIT BUY signal (target) at {price_data.index[i]}")
                        break
        elif position == -1:
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                position = 0
                entry_quantity = 0
                print(f"DEBUG: Generated EXIT SELL signal (stop-loss) at {price_data.index[i]}")
            else:
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], []))
                        position = 0
                        entry_quantity = 0
                        print(f"DEBUG: Generated EXIT SELL signal (target) at {price_data.index[i]}")
                        break

    print("DEBUG:Gann strategy applied successfully.")
    return signals

def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")  # Corrected indentation
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity


def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp, targets in signals:
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}, Targets: {targets}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'targets_hit': []})
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity

                        # Check which long targets were hit
                        for i, target in enumerate(long_trades[-1]['targets']):
                            if exit_price >= target:
                                long_trades[-1]['targets_hit'].append(i + 1)
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity

                        # Check which short targets were hit
                        for i, target in enumerate(short_trades[-1]['targets']):
                            if exit_price <= target:
                                short_trades[-1]['targets_hit'].append(i + 1)

                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp, targets, target_angles in signals:  # Include target_angles
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}, Targets: {targets}, Angles: {target_angles}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'target_angles': target_angles, 'targets_hit': []})  # Add target_angles to long_trades
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'target_angles': target_angles, 'targets_hit': []})  # Add target_angles to short_trades
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity

                        # Check which long targets were hit
                        for i, target in enumerate(long_trades[-1]['targets']):
                            if exit_price >= target:
                                long_trades[-1]['targets_hit'].append(i + 1)
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity

                        # Check which short targets were hit
                        for i, target in enumerate(short_trades[-1]['targets']):
                            if exit_price <= target:
                                short_trades[-1]['targets_hit'].append(i + 1)

                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    # --- Target Hit Metrics ---
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    # Add target hit counts to metrics
    for target_num, hits in target_hits.items():
        metrics[f'target_{target_num}_hits_long'] = hits['long']
        metrics[f'target_{target_num}_hits_short'] = hits['short']

    # --- End of Target Hit Metrics ---

    print("DEBUG: Trading metrics calculated successfully.")

    # Analyze target hit data (optional)
    analyze_target_hits(long_trades, short_trades)

    return metrics, long_trades, short_trades, all_pnls

def analyze_target_hits(long_trades, short_trades):
    """
    Analyzes the frequency of target hits.
    """
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    print("Target Hit Frequency:")
    for target_num, hits in target_hits.items():
        print(f"Target {target_num}: Long - {hits['long']}, Short - {hits['short']}")

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp, targets in signals:
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def calculate_volatility(df, period=7):  # Calculate volatility over 7 periods (e.g., hours) for 1H timeframe
    """
    Calculates the volatility of a stock.
    """
    df['pct_change'] = df['close'].pct_change()
    volatility = df['pct_change'].rolling(window=period).std() * 100  # Convert to percentage
    return volatility.iloc[-1]  # Return the latest volatility value

def get_volatility_range(volatility):
    """
    Determines the volatility range based on volatility value.
    """
    if volatility < 2:
        return 'low'
    elif volatility < 5:
        return 'medium'
    else:
        return 'high'

# --- Volatility-Based Angle Configuration ---
angle_config = {
    'low': [0.125, 0.25, 0.5, 0.75, 1.0],
    'medium': [0.25, 0.5, 1.0, 1.5, 2.0],
    'high': [0.5, 1.0, 2.0, 3.0, 4.0]
}
# --- End of Volatility-Based Angle Configuration ---

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    # --- Calculate Volatility and Get Angles for Targets/SL ---
    volatility = calculate_volatility(df.copy())
    volatility_range = get_volatility_range(volatility)
    target_angles = angle_config.get(volatility_range, angle_config['low'])  # Get angles from config
    # --- End of Volatility and Angle Calculation ---

    signals = gann_strategy(resampled_df, timeframe, target_angles)  # Pass target_angles to gann_strategy
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path


# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# --- Gradio Interface ---
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://4b7481de53fc4c350d.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://4b7481de53fc4c350d.gradio.live


In [ ]:
####################################
# Author: Mahesh Naidu D         ####
# Version: 3.4 (Corrected)       ####
# Strategy Name: Gann square 9  ####
####################################

import pandas as pd
import math
from collections import defaultdict
import matplotlib.pyplot as plt
import os
import numpy as np
import datetime
import gradio as gr

def gann_square_of_9(price, num_levels=5, increment=0.125):
    """
    Calculates Gann Square of 9 values for a given price.
    Handles NaN values gracefully.

    Args:
        price: The price to calculate Gann values for.
        num_levels: The number of Gann levels to calculate.
        increment: The increment to use for calculating Gann levels.

    Returns:
        A list of Gann Square of 9 values.
    """
    print(f"DEBUG: Calculating Gann Square of 9 values for price: {price}, increment: {increment}")
    if math.isnan(price):
        print("DEBUG: Price is NaN, returning an empty list.")
        return []

    root = math.sqrt(price)
    minus_two = root - 2
    rounded = math.ceil(minus_two)

    gann_values = [round((rounded + increment * (i + 1))**2, 2) for i in range(num_levels * 8)]
    print(f"DEBUG: Calculated Gann values: {gann_values}")
    return gann_values

def find_buy_sell_levels(price, gann_values):
    """
    Finds the buy above and sell below levels from Gann values.

    Args:
        price: The current price.
        gann_values: A list of Gann Square of 9 values.

    Returns:
        A tuple containing the buy above and sell below levels.
    """
    print(f"DEBUG: Finding buy/sell levels for price: {price}, Gann values: {gann_values}")
    try:
        buy_above_index = next(i for i, value in enumerate(gann_values) if value > price)
        buy_above = gann_values[buy_above_index]
        sell_below = gann_values[buy_above_index - 1]
        print(f"DEBUG: Buy above: {buy_above}, Sell below: {sell_below}")
    except StopIteration:
        buy_above, sell_below = None, None
        print("DEBUG: No buy/sell levels found.")
    return buy_above, sell_below

def calculate_targets(entry_level, gann_values, direction='long', angles=[0.125, 0.25, 0.5, 0.75, 1.0]):
    """
    Calculates target levels based on trade direction and given angles.
    """
    print(f"DEBUG: Calculating targets for entry level: {entry_level}, direction: {direction}, angles: {angles}")
    if entry_level not in gann_values:
        print("DEBUG: Entry level not found in Gann values.")
        return []

    start_index = gann_values.index(entry_level)
    targets = []
    if direction == 'long':
        for angle in angles:
            target_index = start_index + int(angle * 8)  # Calculate target index based on angle
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])
    elif direction == 'short':
        for angle in angles:
            target_index = start_index - int(angle * 8)
            if 0 <= target_index < len(gann_values):
                targets.append(gann_values[target_index])

    print(f"DEBUG: Calculated targets: {targets}")
    return targets

def gann_strategy(price_data, timeframe, target_angles):
    """
    Implements the Gann strategy with target levels, trailing stop-loss,
    and exit conditions.
    """
    signals = []
    position = 0
    entry_price = 0
    stop_loss_price = 0
    entry_quantity = 0

    volatility = calculate_volatility(price_data)
    volatility_range = get_volatility_range(volatility)
    target_angles = angle_config.get(volatility_range, angle_config['low'])

    for i in range(1, len(price_data) - 1):
        current_price = price_data['close'].iloc[i]
        previous_price = price_data['close'].iloc[i - 1]

        gann_values = gann_square_of_9(previous_price)
        buy_above, sell_below = find_buy_sell_levels(previous_price, gann_values)

        if buy_above and current_price >= buy_above and position == 0:
            entry_price = buy_above
            stop_loss_price = sell_below  # Initial stop-loss
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='long', angles=target_angles)
            signals.append(('buy', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets, target_angles))
            position = 1
        elif sell_below and current_price <= sell_below and position == 0:
            entry_price = sell_below
            stop_loss_price = buy_above  # Initial stop-loss
            entry_quantity = calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price)
            targets = calculate_targets(entry_price, gann_values, direction='short', angles=target_angles)
            signals.append(('sell', entry_price, stop_loss_price, entry_quantity, price_data.index[i], targets, target_angles))
            position = -1

        if position == 1:  # Long position
            if current_price <= stop_loss_price:
                signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], [], []))
                position = 0
                entry_quantity = 0
            else:
                stop_loss_price = max(stop_loss_price, current_price * 0.98)  # Trailing stop-loss
                for target in targets:
                    if current_price >= target:
                        signals.append(('exit_buy', current_price, stop_loss_price, entry_quantity, price_data.index[i], [], []))
                        position = 0
                        entry_quantity = 0
                        break

        elif position == -1:  # Short position
            if current_price >= stop_loss_price:
                signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], [], []))
                position = 0
                entry_quantity = 0
            else:
                stop_loss_price = min(stop_loss_price, current_price * 1.02)  # Trailing stop-loss
                for target in targets:
                    if current_price <= target:
                        signals.append(('exit_sell', current_price, stop_loss_price, entry_quantity, price_data.index[i], [], []))
                        position = 0
                        entry_quantity = 0
                        break

    return signals


def calculate_quantity(capital, entry_price, risk_percentage, stop_loss_price):
    """
    Calculates the quantity of shares/lots to trade based on risk management.

    Args:
        capital: The total trading capital.
        entry_price: The entry price of the trade.
        risk_percentage: The percentage of capital to risk on the trade.
        stop_loss_price: The stop-loss price for the trade.

    Returns:
        The calculated quantity (integer).
    """
    print(f"DEBUG: Calculating quantity for capital: {capital}, entry price: {entry_price}, risk percentage: {risk_percentage}, stop-loss price: {stop_loss_price}")
    risk_amount = capital * (risk_percentage / 100)
    risk_per_share = abs(entry_price - stop_loss_price)
    if risk_per_share == 0:
        print("DEBUG: Risk per share is zero, returning zero quantity.")
        return 0
    quantity = math.floor(risk_amount / risk_per_share)
    print(f"DEBUG: Calculated quantity: {quantity}")
    return quantity

def calculate_metrics(signals, price_data):
    """
    Calculates trading metrics based on the generated signals.

    Args:
        signals: A list of signals generated by the gann_strategy function.
        price_data: A pandas DataFrame with 'close' price data and a datetime index.

    Returns:
        A dictionary of trading metrics.
    """
    print("DEBUG: Calculating trading metrics.")
    metrics = defaultdict(int)
    long_trades = []
    short_trades = []
    long_pnl = []
    short_pnl = []
    all_pnls = []

    position = 0
    entry_price = 0
    entry_time = None
    entry_quantity = 0

    for signal, entry_level, stop_loss_price, quantity, timestamp, targets, target_angles in signals:  # Include target_angles
        try:
            print(f"DEBUG: Signal: {signal}, Entry Level: {entry_level}, Stop Loss: {stop_loss_price}, Timestamp: {timestamp}, Quantity: {quantity}, Targets: {targets}, Angles: {target_angles}")
            if signal == 'buy' and position == 0:
                position = 1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                long_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'target_angles': target_angles, 'targets_hit': []})  # Add target_angles to long_trades
                print(f"DEBUG: Processing BUY signal at {timestamp}")
            elif signal == 'sell' and position == 0:
                position = -1
                entry_price = entry_level
                entry_time = timestamp
                entry_quantity = quantity
                short_trades.append({'entry_time': entry_time, 'entry_price': entry_price, 'stop_loss_price': stop_loss_price, 'quantity': quantity, 'targets': targets, 'target_angles': target_angles, 'targets_hit': []})  # Add target_angles to short_trades
                print(f"DEBUG: Processing SELL signal at {timestamp}")
            elif signal.startswith('exit') and position != 0:
                if (position == 1 and long_trades) or (position == -1 and short_trades):
                    exit_price = price_data['close'].loc[timestamp]
                    if position == 1:
                        pnl = (exit_price - entry_price) * entry_quantity

                        # Check which long targets were hit
                        for i, target in enumerate(long_trades[-1]['targets']):
                            if exit_price >= target:
                                long_trades[-1]['targets_hit'].append(i + 1)
                    else:
                        pnl = (entry_price - exit_price) * entry_quantity

                        # Check which short targets were hit
                        for i, target in enumerate(short_trades[-1]['targets']):
                            if exit_price <= target:
                                short_trades[-1]['targets_hit'].append(i + 1)

                    all_pnls.append(pnl)

                    if position == 1:
                        long_trades[-1]['exit_time'] = timestamp
                        long_trades[-1]['exit_price'] = exit_price
                        long_trades[-1]['pnl'] = pnl
                        metrics['long_trades'] += 1
                        metrics['long_pnl'] += pnl
                        long_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT BUY signal at {timestamp}")
                    else:
                        short_trades[-1]['exit_time'] = timestamp
                        short_trades[-1]['exit_price'] = exit_price
                        short_trades[-1]['pnl'] = pnl
                        metrics['short_trades'] += 1
                        metrics['short_pnl'] += pnl
                        short_pnl.append(pnl)
                        print(f"DEBUG: Processing EXIT SELL signal at {timestamp}")
                    position = 0
                else:
                    print(f"DEBUG: Ignoring {signal} signal at {timestamp} - No open trade.")
        except Exception as e:
            print(f"DEBUG: Error processing signal: {signal}, Error: {e}")

    metrics['total_trades'] = metrics['long_trades'] + metrics['short_trades']
    metrics['total_pnl'] = metrics['long_pnl'] + metrics['short_pnl']

    long_wins = 0
    short_wins = 0

    if metrics['long_trades'] > 0:
        metrics['avg_long_pnl'] = metrics['long_pnl'] / metrics['long_trades']
        long_wins = sum(1 for p in long_pnl if p > 0)
        metrics['long_win_rate'] = long_wins / metrics['long_trades'] if metrics['long_trades'] > 0 else 0
    else:
        metrics['avg_long_pnl'] = 0
        metrics['long_win_rate'] = 0

    if metrics['short_trades'] > 0:
        metrics['avg_short_pnl'] = metrics['short_pnl'] / metrics['short_trades']
        short_wins = sum(1 for p in short_pnl if p > 0)
        metrics['short_win_rate'] = short_wins / metrics['short_trades'] if metrics['short_trades'] > 0 else 0
    else:
        metrics['avg_short_pnl'] = 0
        metrics['short_win_rate'] = 0

    metrics['winning_trades'] = long_wins + short_wins
    metrics['losing_trades'] = metrics['total_trades'] - metrics['winning_trades']
    metrics['winning_percentage'] = metrics['winning_trades'] / metrics['total_trades'] if metrics['total_trades'] > 0 else 0

    if len(all_pnls) > 1:
        returns = pd.Series(all_pnls)
        metrics['sharpe_ratio'] = returns.mean() / returns.std() if returns.std() != 0 else 0
        negative_returns = returns[returns < 0]
        metrics['sortino_ratio'] = returns.mean() / negative_returns.std() if negative_returns.std() != 0 else 0
    else:
        metrics['sharpe_ratio'] = 0
        metrics['sortino_ratio'] = 0

    # --- Target Hit Metrics ---
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    # Add target hit counts to metrics
    for target_num, hits in target_hits.items():
        metrics[f'target_{target_num}_hits_long'] = hits['long']
        metrics[f'target_{target_num}_hits_short'] = hits['short']

    # --- End of Target Hit Metrics ---

    print("DEBUG: Trading metrics calculated successfully.")

    # Analyze target hit data (optional)
    analyze_target_hits(long_trades, short_trades)

    return metrics, long_trades, short_trades, all_pnls

def analyze_target_hits(long_trades, short_trades):
    """
    Analyzes the frequency of target hits.
    """
    target_hits = defaultdict(lambda: {'long': 0, 'short': 0})

    for trade in long_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['long'] += 1

    for trade in short_trades:
        for target_num in trade['targets_hit']:
            target_hits[target_num]['short'] += 1

    print("Target Hit Frequency:")
    for target_num, hits in target_hits.items():
        print(f"Target {target_num}: Long - {hits['long']}, Short - {hits['short']}")

def plot_candlestick_chart(df, signals, timeframe, scrip_symbol, save_path):
    """
    Plots a candlestick chart with buy/sell signals.

    Args:
        df: The DataFrame containing OHLCV data.
        signals: The list of signals generated by the strategy.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the chart image.
    """
    print("DEBUG: Plotting candlestick chart.")
    fig, ax = plt.subplots(figsize=(12, 6))

    # Plot candlesticks
    width = 0.6
    width2 = 0.1
    up = df[df.close >= df.open]
    down = df[df.close < df.open]
    ax.bar(up.index, up.close - up.open, width, bottom=up.open, color="green")
    ax.bar(up.index, up.high - up.close, width2, bottom=up.close, color="green")
    ax.bar(up.index, up.low - up.open, width2, bottom=up.open, color="green")
    ax.bar(down.index, down.close - down.open, width, bottom=down.open, color="red")
    ax.bar(down.index, down.high - down.open, width2, bottom=down.open, color="red")
    ax.bar(down.index, down.low - down.close, width2, bottom=down.close, color="red")

    # Plot buy/sell signals
    for signal, entry_price, stop_loss_price, quantity, timestamp, targets, target_angles in signals:  # Include target_angles
        if signal == 'buy':
            ax.plot(timestamp, entry_price, '^', markersize=10, color='g', label='Buy')
        elif signal == 'sell':
            ax.plot(timestamp, entry_price, 'v', markersize=10, color='r', label='Sell')

    ax.set_title(f"{scrip_symbol} Candlestick Chart with Gann Signals ({timeframe})")
    ax.set_xlabel("Date")
    ax.set_ylabel("Price")
    ax.legend()

    # Save the chart
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}.png"))
    plt.close(fig)
    print("DEBUG: Candlestick chart plotted and saved successfully.")


def plot_pnl_curve(pnls, timeframe, scrip_symbol, save_path):
    """
    Plots the PnL curve and saves it to a file.
    Args:
        pnls: A list of PnLs.
        timeframe: The timeframe of the data.
        scrip_symbol: The symbol of the scrip (stock).
        save_path: The path to save the PnL curve image.
    """
    print("DEBUG: Plotting PnL curve.")
    cumulative_pnls = np.cumsum(pnls)
    plt.figure(figsize=(12, 6))
    plt.plot(cumulative_pnls)
    plt.title(f"{scrip_symbol} PnL Curve ({timeframe})")
    plt.xlabel("Trades")
    plt.ylabel("Cumulative PnL")

    plt.savefig(os.path.join(save_path, f"{scrip_symbol}_{timeframe}_pnl_curve.png"))
    plt.close()
    print("DEBUG: PnL curve plotted and saved successfully.")

def resample_data(df, timeframe):
    """
    Resamples the DataFrame to the specified timeframe, aligned with Indian market hours (9:15 - 15:30).

    Parameters:
        df (pd.DataFrame): The input DataFrame with a datetime index.
        timeframe (str): The desired timeframe (e.g., '30min', '1H', '5min', '15min').

    Returns:
        pd.DataFrame: Resampled DataFrame.
    """
    print(f"DEBUG: Resampling data for timeframe: {timeframe}")
    if df.index.tz is None:
        df.index = df.index.tz_localize('Asia/Kolkata')
    else:
        df.index = df.index.tz_convert('Asia/Kolkata')

    df = df.between_time('9:15', '15:30')

    if timeframe == '30min':
        df_resampled = df.resample('30min', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    elif timeframe == '1H':
        df_resampled = df.resample('1h', origin='epoch', offset='9h15min').agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })
    else:
        df_resampled = df.resample(timeframe).agg({
            'open': 'first',
            'high': 'max',
            'low': 'min',
            'close': 'last',
            'volume': 'sum'
        })

    df_resampled = df_resampled.dropna(subset=['open', 'close'])
    print("DEBUG: Data resampled successfully.")
    return df_resampled

def calculate_volatility(df, period=7):  # Calculate volatility over 7 periods (e.g., hours) for 1H timeframe
    """
    Calculates the volatility of a stock.
    """
    df['pct_change'] = df['close'].pct_change()
    volatility = df['pct_change'].rolling(window=period).std() * 100  # Convert to percentage
    return volatility.iloc[-1]  # Return the latest volatility value

def get_volatility_range(volatility):
    """
    Determines the volatility range based on volatility value.
    """
    if volatility < 2:
        return 'low'
    elif volatility < 5:
        return 'medium'
    else:
        return 'high'

# --- Volatility-Based Angle Configuration ---
angle_config = {
    'low': [0.125, 0.25, 0.5, 0.75, 1.0],
    'medium': [0.25, 0.5, 1.0, 1.5, 2.0],
    'high': [0.5, 1.0, 2.0, 3.0, 4.0]
}
# --- End of Volatility-Based Angle Configuration ---

def analyze_stock(stock_name, timeframe='5min'):
    """
    Analyzes the selected stock and timeframe using the Gann strategy.

    Args:
        stock_name: The name of the stock (folder name).
        timeframe: The selected timeframe.

    Returns:
        A tuple containing the metrics DataFrame, trades DataFrame,
        candlestick chart image path, and PNL curve image path.
    """
    print(f"DEBUG: Analyzing stock: {stock_name}, timeframe: {timeframe}")
    data_dir = "/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data"
    stock_path = os.path.join(data_dir, stock_name)

    file_path = os.path.join(stock_path, f"{stock_name}.parquet")
    save_path = os.path.join(data_dir, f"Gann_Charts/{stock_name}")
    metrics_path = os.path.join(save_path, f"{stock_name}_metrics.csv")
    trades_path = os.path.join(save_path, f"{stock_name}_{timeframe}_trades.csv")
    chart_path = os.path.join(save_path, f"{stock_name}_{timeframe}.png")
    pnl_path = os.path.join(save_path, f"{stock_name}_{timeframe}_pnl_curve.png")

    try:
        df = pd.read_parquet(file_path)
    except FileNotFoundError:
        print(f"Error: Data file not found for {stock_name} at {file_path}")
        return None, None, None, None

    df = df.rename(columns={'datetime': 'date'})
    df['date'] = pd.to_datetime(df['date'])
    df.set_index('date', inplace=True)

    resampled_df = resample_data(df.copy(), timeframe)

    # --- Calculate Volatility and Get Angles for Targets/SL ---
    volatility = calculate_volatility(df.copy())
    volatility_range = get_volatility_range(volatility)
    target_angles = angle_config.get(volatility_range, angle_config['low'])  # Get angles from config
    # --- End of Volatility and Angle Calculation ---

    signals = gann_strategy(resampled_df, timeframe, target_angles)  # Pass target_angles to gann_strategy
    metrics, long_trades, short_trades, all_pnls = calculate_metrics(signals, resampled_df)
    all_metrics = {timeframe: metrics}

    trades_list = []
    for trade in long_trades:
        trade['trade_type'] = 'long'
        trades_list.append(trade)
    for trade in short_trades:
        trade['trade_type'] = 'short'
        trades_list.append(trade)

    all_trades_df = pd.DataFrame(trades_list)

    plot_candlestick_chart(resampled_df, signals, timeframe, stock_name, save_path)
    plot_pnl_curve(all_pnls, timeframe, stock_name, save_path)

    metrics_df = pd.DataFrame(all_metrics).transpose()
    metrics_df.to_csv(metrics_path, index=False)
    all_trades_df.to_csv(trades_path, index=False)

    metrics_df = pd.read_csv(metrics_path)
    trades_df = pd.read_csv(trades_path)

    print(f"DEBUG: Analysis completed for stock: {stock_name}, timeframe: {timeframe}")
    return metrics_df, all_trades_df, chart_path, pnl_path

# --- Main Execution ---
# Get the list of stocks (folder names)
stock_list = [f for f in os.listdir("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data") if os.path.isdir(os.path.join("/content/drive/MyDrive/BACKTEST/stock-1min/stock_min_data", f))]

capital = 100000  # Set your initial capital
risk_percentage = 1  # Set the percentage of capital to risk per trade

# --- Gradio Interface ---
iface = gr.Interface(
    fn=analyze_stock,
    inputs=[
        gr.Dropdown(choices=stock_list, label="Select Stock"),
        gr.Dropdown(choices=['5min', '15min', '30min', '1H'], label="Select Timeframe", value='5min')
    ],
    outputs=[
        gr.Dataframe(label="Metrics"),
        gr.Dataframe(label="Trades"),
        gr.Image(label="Candlestick Chart", type="filepath"),
        gr.Image(label="PNL Curve", type="filepath")
    ],
    title="Gann Strategy Backtesting"
)

iface.launch(debug=True)

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://edc5adf6d0112080ba.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Streaming output truncated to the last 5000 lines.
DEBUG: Calculated Gann values: [12348.77, 12376.56, 12404.39, 12432.25, 12460.14, 12488.06, 12516.02, 12544.0, 12572.02, 12600.06, 12628.14, 12656.25, 12684.39, 12712.56, 12740.77, 12769.0, 12797.27, 12825.56, 12853.89, 12882.25, 12910.64, 12939.06, 12967.52, 12996.0, 13024.52, 13053.06, 13081.64, 13110.25, 13138.89, 13167.56, 13196.27, 13225.0, 13253.77, 13282.56, 13311.39, 13340.25, 13369.14, 13398.06, 13427.02, 13456.0]
DEBUG: Finding buy/sell levels for price: 12550.0, Gann values: [12348.77, 12376.56, 12404.39, 12432.25, 12460.14, 12488.06, 12516.02, 12544.0, 12572.02, 12600.06, 12628.14, 12656.25, 12684.39, 12712.56, 12740.77, 12769.0, 12797.27, 12825.56, 12853.89, 12882.25, 12910.64, 12939.06, 12967.52, 12996.0, 13024.52, 13053.06, 13081.64, 13110.25, 13138.89, 13167.56, 13196.27, 13225.0, 13253.77, 13282.56, 13311.39, 13340.25, 13369.14, 13398.06, 13427.02, 13456.0]
DEBUG: Buy above: 12572.02, Sell below: 12544.0
DEBUG: Calcula